Dataset includes several time series representing different ATMs and their daily cash money demand at different locations.

In [1]:
# NOTE FIX THESE IMPORTS

from data_loader import convert_tsf_to_dataframe
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import statsmodels.api as sm
import math
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.nn.functional import linear, softmax
from torch.nn.modules.linear import NonDynamicallyQuantizableLinear
from torch import Tensor
from typing import Optional, Tuple, Union, Callable, Any, List
from torch.nn.init import xavier_uniform_, constant_, xavier_normal_
import copy
from torch.nn import Module, LayerNorm, ModuleList
from torch.nn.parameter import Parameter
import datetime
from torch.utils.data import Dataset, DataLoader
import sys

In [2]:
torch.set_printoptions(threshold=1000)

In [3]:
TSF_FILE = 'nn5_daily_dataset_with_missing_values.tsf'

In [4]:
data = convert_tsf_to_dataframe(TSF_FILE)

In [5]:
series_values = data[0]['series_value']

In [ ]:
data

In [ ]:
data[0]

In [ ]:
data[0]['series_value'][0]

In [ ]:
date_range_0 = pd.date_range(start='1996-03-18', periods=791, freq='D')

In [ ]:
date_range_0

In [ ]:
data_0 = pd.DataFrame({'series_value': data[0]['series_value'][0], 'date': date_range_0})
data_0 = data_0.set_index('date')

In [ ]:
data_0

In [ ]:
plt.plot(data_0['series_value'][:21])

In [ ]:
np.array(data_0['series_value'])

In [ ]:
# proportion of nulls and zeroes
total = 791 * 111
null_count = 0
zero_count = 0
for i in range(len(data[0]['series_value'])):
    series_values = np.array(pd.to_numeric(data[0]['series_value'][i], errors='coerce'))
    nulls_in_series = np.sum(np.isnan(series_values))
    null_count += nulls_in_series
    zeroes_in_series = len(series_values) - np.count_nonzero(series_values)
    zero_count += zeroes_in_series
(null_count + zero_count) / total
    

Questions and notes:

- Global methods seem better than traditional univariate methods for this dataset because we can leverage related but seperate datasets in a unified model. Traditional methods such as ARIMA do not have this capability and if we would need to fit a separate model for each dataset. (Look into this).  


- How to deal with missing values? I assume if we're using a deep learning method, we could simply treat the missing values as breakpoints for training samples. I.e. let's say you have \[$x_1$, $x_2$, $x_3$, $x_4$, $x_5$, $x_6$, $x_7$, $x_8$\] where this is a sequence in order of time and $x_5$ is missing. Then, assuming the model uses a lag of 2, we can treat {$X$: \[$x_1$, $x_2$\], $y$: $x_3$}, {$X$: \[$x_2$, $x_3$\], $y$: $x_4$} and {$X$: \[$x_6$, $x_7$\], $y$: $x_8$} as our training examples, treating $x_5$ as a breakpoint. Is there a better way? ANSWER: for now no need to interpolate missing data, let's just try training on what we have.


- How can we identify the types of seasonality in the data? Can we deal with multiple seasonality? Traditional seasonal decomposition methods (even those which deal with multiple seasonality i.e. MSTL) will probably not work too well due to the multiple series. How do we integrate seasonality into the model? One idea is to use sin/cos encodings depending on the seasonal position. I.e. for seasonality that occurs one day a week, use $a\sin (x\cdot \frac{\pi}{3.5})$ and the cos version, where $a$ is tuneable. But how many of these terms should we include? Seems like a relatively wieldy hyperparameter. Also, if we need to see how to modify the architecture to include these terms. Another idea is to include the previous season's data, i.e. alongside the $k$ lags from the past we use $x_{t - p}$ as input, where $p$ is the seasonal period. Note that we would also need some kind of positional encoding for this value. Perhaps try dealing with seasonality after an original attempt without it, though.


- TODO: I want to try applying a transformer model to this data, research and look into transformers. From there we can try different things. So first just try applying a vanilla transformer. 
    - BUT WAIT... is the transformer really the best choice here? The problem I see with the transformer is that it is more suited for sequence-to-sequence models. In other words, you get one complete sequence as input and have to output another related sequence. Perhaps there is some modification to this that allows for completion of one sequence but anyway, if I'm correct, the self-attention used in the transformer will not be applicable to numerical time series such as this one. When it comes to sequence-to-sequence models that the transformer is meant for, the words can influence each other, i.e. a word later in the sequence can provide semantic information about a word earlier in the sequence, and self-attention deals with that scenario, where the information flow is not necessarily left-to-right. But for a time series like this, the information flows unidirectionally, elements earlier in the sequence do not depend on elements later in the sequence. Using a self-attention encoding where all elements of the sequence attend on each other would lead to spurious modelling. Perhaps an RNN model would be more suited to this kind of time series data. I will look into deep learning models for time series and find something that makes sense. 



- Better way to decode? Right now training uses "teacher forcing", but inference does not, if a very wrong prediction is produced then it negatively affects the subsequent predictions that get decoded, and without a concept of sequence probability we can't use beam search. Perhaps predict everything at once, i.e. no autoregressive decoding (which is needed for NLP because you don't know when the sequence will end, but we know the desired forecast horizon for time series). New "decoder" takes timestep position, performs some positional embedding, computes attention on encoder output, depending on query generated from positional embedding, performs transformations on the values and outputs the desired number of forecasts, one for each positional embedding. Something to try. Note this could possibly also enable forecasting of variable length for a single trained model depending on how I implement the positional encodings. If I use a lookup table for the positional encodings this is impossible, but if I use matrix mulitplications with the raw timestep number it is possible.


- Seasonailty: first create a seasonal encoder. Essentially given a forecast horizon, i.e. 7, and a hyperparameter for window size, i.e. 5, we create a "seasonal context" of len (horizon + window_sz) - 1. In other words, we take all our desired dates to forecast, seasonally shifted, get those values, as well as the (window_sz - 1) / 2 values on each side. So we have our seasonal context, comprised of horizon_len windows of length window_sz. Example: if our context is \[1, 2, 3, 4, 5\] and our window_sz is 3 (meaning we want to forecast 3 into the future), we have 3 windows \[1, 2, 3\], \[2, 3, 4\], and \[3, 4, 5\]. One corresponding to each position we want to decode. The intuition is that we hope each window contains seasonal data relevant to each date we want to forecast. We encode this seasonal context with its own learned position embeddings and weights; encoder is our modified encoder with causal self attention. Once the self attention finishes, we get a matrix of size (context_len x d_season). Normally we would then use the decoder-encoder attention as in the normal transformer but the problem here is that if we want to use this with the modified decoder as above, we can't do this. The decoder inputs for the modified decoder are merely timestep encodings so I'm not sure if that will give enough information to attend to the seasonal context, but I should probably try it nonetheless. My idea is to first perform attention from the decoder timestep encodings to the encodings of the previous $k$ time series elements immediately preceding the dates we want to forecast. Then we attend from the output of this to the seasonal encodings, applying as mask (see notes) before the softmax so that each decoder position only attends to the corresponding window for each season. We perform this attention on each seasonal component at the same time by concatentating the keys along the position axis. From here we get the regular dimension of values which we transform to get all the decoder timesteps at once. 


- Think about feeature engineering


- How to deal with nulls in target? I.e. how do we remove these from loss? We might still have to discard data... Like if at timestep 3 in the decoder the ground truth isn't available, i.e. null, how can we compute the loss and keep it differentiable? 
    - I suppose we could impute the null value in the target to be the same as the previous value or something. Not ideal but will be differentiable at least
    - Pytorch has a reduce flag in loss which lets you do perform loss elementwise. Idea is that we remove the nulls after doing this, and average the rest. But is this differentiable? Well apparently it's somehow differentiable but some of the gradients become null
    
    
- Perhaps I should apply some sort of clustering method. It seems like each ATM is at a different location, so the location itself is a latent variable that is not explicitly included. Different locations and location types may look different. Clustering could deal with this, use a different model for each cluster. Hopefully these inherent location differences get picked up by the clustering method. Look into time series clustering. 


- Here's the plan: try a variety of different models, and forecast for 1-day, 2-days, ..., 7-days ahead

- Models to consider:
    - ARIMA (baseline)
    - LSTM
    - Transformer
    - Temporal fusion transformer


- Transformer ideas:
    - Deal with nulls by setting them to 0 and applying an (input) mask which we add before the softmax which makes the null components of the self-attention negative infinity, becoming 0 after the softmax, thus negating their attention weights and ensuring they do not factor in to the final result. Experimentally verified that this does not affect the backprop computation (null component has 0 gradient in query/key matrices). 
        - Note that we also have to mask out the row of the queries for the null value, only way I can think of to do this is to first let the softmax do its thing on the row of 0's, then remove the row (using the null timestep dim input), and add in a row of 0's at the deleted position. Wouldn't this break the differentiable graph though? Perhaps there's no need to do this after all. Let's verify. Yes, we don't need to do the initial removal from the softmax tensor, we can simply add a mask in the decoding component which masks out the encoding corresponding to null in its attention
    - Mask out future timesteps during encoding. I.e. make the encoder self attention autoregressive by applying an encoding mask. Deals with the issue mentioned above. So the encoding at position 2 can only be affected by positions 1 and 2, etc.
    

In [ ]:
# Trying vanilla transformer from pytorch with adaptations

In [6]:

def _in_projection_packed(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    w: Tensor,
    b: Optional[Tensor] = None,
) -> List[Tensor]:
    r"""
    Performs the in-projection step of the attention operation, using packed weights.
    Output is a triple containing projection tensors for query, key and value.
    Args:
        q, k, v: query, key and value tensors to be projected. For self-attention,
            these are typically the same tensor; for encoder-decoder attention,
            k and v are typically the same tensor. (We take advantage of these
            identities for performance if they are present.) Regardless, q, k and v
            must share a common embedding dimension; otherwise their shapes may vary.
        w: projection weights for q, k and v, packed into a single tensor. Weights
            are packed along dimension 0, in q, k, v order.
        b: optional projection biases for q, k and v, packed into a single tensor
            in q, k, v order.
    Shape:
        Inputs:
        - q: :math:`(..., E)` where E is the embedding dimension
        - k: :math:`(..., E)` where E is the embedding dimension
        - v: :math:`(..., E)` where E is the embedding dimension
        - w: :math:`(E * 3, E)` where E is the embedding dimension
        - b: :math:`E * 3` where E is the embedding dimension
        Output:
        - in output list :math:`[q', k', v']`, each output tensor will have the
            same shape as the corresponding input tensor.
    """
    E = q.size(-1)
    if k is v:
        if q is k:
            # self-attention
            return linear(q, w, b).chunk(3, dim=-1)
        else:
            # encoder-decoder attention
            w_q, w_kv = w.split([E, E * 2])
            if b is None:
                b_q = b_kv = None
            else:
                b_q, b_kv = b.split([E, E * 2])
            return (linear(q, w_q, b_q),) + linear(k, w_kv, b_kv).chunk(2, dim=-1)
    else:
        w_q, w_k, w_v = w.chunk(3)
        if b is None:
            b_q = b_k = b_v = None
        else:
            b_q, b_k, b_v = b.chunk(3)
        return linear(q, w_q, b_q), linear(k, w_k, b_k), linear(v, w_v, b_v)

    
def _in_projection(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    w_q: Tensor,
    w_k: Tensor,
    w_v: Tensor,
    b_q: Optional[Tensor] = None,
    b_k: Optional[Tensor] = None,
    b_v: Optional[Tensor] = None,
) -> Tuple[Tensor, Tensor, Tensor]:
    r"""
    Performs the in-projection step of the attention operation. This is simply
    a triple of linear projections, with shape constraints on the weights which
    ensure embedding dimension uniformity in the projected outputs.
    Output is a triple containing projection tensors for query, key and value.
    Args:
        q, k, v: query, key and value tensors to be projected.
        w_q, w_k, w_v: weights for q, k and v, respectively.
        b_q, b_k, b_v: optional biases for q, k and v, respectively.
    Shape:
        Inputs:
        - q: :math:`(Qdims..., Eq)` where Eq is the query embedding dimension and Qdims are any
            number of leading dimensions.
        - k: :math:`(Kdims..., Ek)` where Ek is the key embedding dimension and Kdims are any
            number of leading dimensions.
        - v: :math:`(Vdims..., Ev)` where Ev is the value embedding dimension and Vdims are any
            number of leading dimensions.
        - w_q: :math:`(Eq, Eq)`
        - w_k: :math:`(Eq, Ek)`
        - w_v: :math:`(Eq, Ev)`
        - b_q: :math:`(Eq)`
        - b_k: :math:`(Eq)`
        - b_v: :math:`(Eq)`
        Output: in output triple :math:`(q', k', v')`,
         - q': :math:`[Qdims..., Eq]`
         - k': :math:`[Kdims..., Eq]`
         - v': :math:`[Vdims..., Eq]`
    """
    Eq, Ek, Ev = q.size(-1), k.size(-1), v.size(-1)
    assert w_q.shape == (Eq, Eq), f"expecting query weights shape of {(Eq, Eq)}, but got {w_q.shape}"
    assert w_k.shape == (Eq, Ek), f"expecting key weights shape of {(Eq, Ek)}, but got {w_k.shape}"
    assert w_v.shape == (Eq, Ev), f"expecting value weights shape of {(Eq, Ev)}, but got {w_v.shape}"
    assert b_q is None or b_q.shape == (Eq,), f"expecting query bias shape of {(Eq,)}, but got {b_q.shape}"
    assert b_k is None or b_k.shape == (Eq,), f"expecting key bias shape of {(Eq,)}, but got {b_k.shape}"
    assert b_v is None or b_v.shape == (Eq,), f"expecting value bias shape of {(Eq,)}, but got {b_v.shape}"
    return linear(q, w_q, b_q), linear(k, w_k, b_k), linear(v, w_v, b_v)



def _scaled_dot_product_attention(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    attn_mask: Optional[Tensor] = None,
    dropout_p: float = 0.0,
) -> Tuple[Tensor, Tensor]:
    r"""
    Computes scaled dot product attention on query, key and value tensors, using
    an optional attention mask if passed, and applying dropout if a probability
    greater than 0.0 is specified.
    Returns a tensor pair containing attended values and attention weights.
    Args:
        q, k, v: query, key and value tensors. See Shape section for shape details.
        attn_mask: optional tensor containing mask values to be added to calculated
            attention. May be 2D or 3D; see Shape section for details.
        dropout_p: dropout probability. If greater than 0.0, dropout is applied.
    Shape:
        - q: :math:`(B, Nt, E)` where B is batch size, Nt is the target sequence length,
            and E is embedding dimension.
        - key: :math:`(B, Ns, E)` where B is batch size, Ns is the source sequence length,
            and E is embedding dimension.
        - value: :math:`(B, Ns, E)` where B is batch size, Ns is the source sequence length,
            and E is embedding dimension.
        - attn_mask: either a 3D tensor of shape :math:`(B, Nt, Ns)` or a 2D tensor of
            shape :math:`(Nt, Ns)`.
        - Output: attention values have shape :math:`(B, Nt, E)`; attention weights
            have shape :math:`(B, Nt, Ns)`
    """
    B, Nt, E = q.shape
    q = q / math.sqrt(E)

    # (B, Nt, E) x (B, E, Ns) -> (B, Nt, Ns)
    if attn_mask is not None:
        attn = torch.baddbmm(attn_mask, q, k.transpose(-2, -1))
    else:
        attn = torch.bmm(q, k.transpose(-2, -1))
    
#     print('attn before soft')
#     print(attn)
    attn = softmax(attn, dim=-1)
#     print('attn after soft')
#     print(attn)

    if dropout_p > 0.0:
        attn = F.dropout(attn, p=dropout_p)
    # (B, Nt, Ns) x (B, Ns, E) -> (B, Nt, E)
    output = torch.bmm(attn, v)
#     print('attn output')
#     print(output)
    return output, attn



def multi_head_attention_forward(
    query: Tensor,
    key: Tensor,
    value: Tensor,
    embed_dim_to_check: int,
    num_heads: int,
    in_proj_weight: Optional[Tensor],
    in_proj_bias: Optional[Tensor],
    bias_k: Optional[Tensor],
    bias_v: Optional[Tensor],
    add_zero_attn: bool,
    dropout_p: float,
    out_proj_weight: Tensor,
    out_proj_bias: Optional[Tensor],
    training: bool = True,
    key_padding_mask: Optional[Tensor] = None,
    need_weights: bool = True,
    attn_mask: Optional[Tensor] = None,
    use_separate_proj_weight: bool = False,
    q_proj_weight: Optional[Tensor] = None,
    k_proj_weight: Optional[Tensor] = None,
    v_proj_weight: Optional[Tensor] = None,
    static_k: Optional[Tensor] = None,
    static_v: Optional[Tensor] = None,
    average_attn_weights: bool = True,
    is_batched: bool = True,
) -> Tuple[Tensor, Optional[Tensor]]:
    r"""
    Args:
        query, key, value: map a query and a set of key-value pairs to an output.
            See "Attention Is All You Need" for more details.
        embed_dim_to_check: total dimension of the model.
        num_heads: parallel attention heads.
        in_proj_weight, in_proj_bias: input projection weight and bias.
        bias_k, bias_v: bias of the key and value sequences to be added at dim=0.
        add_zero_attn: add a new batch of zeros to the key and
                       value sequences at dim=1.
        dropout_p: probability of an element to be zeroed.
        out_proj_weight, out_proj_bias: the output projection weight and bias.
        training: apply dropout if is ``True``.
        key_padding_mask: if provided, specified padding elements in the key will
            be ignored by the attention. This is an binary mask. When the value is True,
            the corresponding value on the attention layer will be filled with -inf.
        need_weights: output attn_output_weights.
        attn_mask: 2D or 3D mask that prevents attention to certain positions. A 2D mask will be broadcasted for all
            the batches while a 3D mask allows to specify a different mask for the entries of each batch.
        use_separate_proj_weight: the function accept the proj. weights for query, key,
            and value in different forms. If false, in_proj_weight will be used, which is
            a combination of q_proj_weight, k_proj_weight, v_proj_weight.
        q_proj_weight, k_proj_weight, v_proj_weight, in_proj_bias: input projection weight and bias.
        static_k, static_v: static key and value used for attention operators.
        average_attn_weights: If true, indicates that the returned ``attn_weights`` should be averaged across heads.
            Otherwise, ``attn_weights`` are provided separately per head. Note that this flag only has an effect
            when ``need_weights=True.``. Default: True
    Shape:
        Inputs:
        - query: :math:`(L, E)` or :math:`(L, N, E)` where L is the target sequence length, N is the batch size, E is
          the embedding dimension.
        - key: :math:`(S, E)` or :math:`(S, N, E)`, where S is the source sequence length, N is the batch size, E is
          the embedding dimension.
        - value: :math:`(S, E)` or :math:`(S, N, E)` where S is the source sequence length, N is the batch size, E is
          the embedding dimension.
        - key_padding_mask: :math:`(S)` or :math:`(N, S)` where N is the batch size, S is the source sequence length.
          If a ByteTensor is provided, the non-zero positions will be ignored while the zero positions
          will be unchanged. If a BoolTensor is provided, the positions with the
          value of ``True`` will be ignored while the position with the value of ``False`` will be unchanged.
        - attn_mask: 2D mask :math:`(L, S)` where L is the target sequence length, S is the source sequence length.
          3D mask :math:`(N*num_heads, L, S)` where N is the batch size, L is the target sequence length,
          S is the source sequence length. attn_mask ensures that position i is allowed to attend the unmasked
          positions. If a ByteTensor is provided, the non-zero positions are not allowed to attend
          while the zero positions will be unchanged. If a BoolTensor is provided, positions with ``True``
          are not allowed to attend while ``False`` values will be unchanged. If a FloatTensor
          is provided, it will be added to the attention weight.
        - static_k: :math:`(N*num_heads, S, E/num_heads)`, where S is the source sequence length,
          N is the batch size, E is the embedding dimension. E/num_heads is the head dimension.
        - static_v: :math:`(N*num_heads, S, E/num_heads)`, where S is the source sequence length,
          N is the batch size, E is the embedding dimension. E/num_heads is the head dimension.
        Outputs:
        - attn_output: :math:`(L, E)` or :math:`(L, N, E)` where L is the target sequence length, N is the batch size,
          E is the embedding dimension.
        - attn_output_weights: Only returned when ``need_weights=True``. If ``average_attn_weights=True``, returns
          attention weights averaged across heads of shape :math:`(L, S)` when input is unbatched or
          :math:`(N, L, S)`, where :math:`N` is the batch size, :math:`L` is the target sequence length, and
          :math:`S` is the source sequence length. If ``average_weights=False``, returns attention weights per
          head of shape :math:`(num_heads, L, S)` when input is unbatched or :math:`(N, num_heads, L, S)`.
    """
    
#     print('query')
#     print(query)
#     print('key')
#     print(key)
#     print('value')
#     print(value)
    
    
    # For unbatched input, we unsqueeze at the expected batch-dim to pretend that the input
    # is batched, run the computation and before returning squeeze the
    # batch dimension so that the output doesn't carry this temporary batch dimension.
    if not is_batched:
        # unsqueeze if the input is unbatched
        query = query.unsqueeze(1)
        key = key.unsqueeze(1)
        value = value.unsqueeze(1)
        if key_padding_mask is not None:
            key_padding_mask = key_padding_mask.unsqueeze(0)

    # set up shape vars
    tgt_len, bsz, embed_dim = query.shape
    src_len, _, _ = key.shape
    assert embed_dim == embed_dim_to_check, \
        f"was expecting embedding dimension of {embed_dim_to_check}, but got {embed_dim}"
    
    head_dim = embed_dim // num_heads
    assert head_dim * num_heads == embed_dim, f"embed_dim {embed_dim} not divisible by num_heads {num_heads}"
    if use_separate_proj_weight:
        # allow MHA to have different embedding dimensions when separate projection weights are used
        assert key.shape[:2] == value.shape[:2], \
            f"key's sequence and batch dims {key.shape[:2]} do not match value's {value.shape[:2]}"
    else:
        assert key.shape == value.shape, f"key shape {key.shape} does not match value shape {value.shape}"

    #
    # compute in-projection
    #
 
    if not use_separate_proj_weight:
        assert in_proj_weight is not None, "use_separate_proj_weight is False but in_proj_weight is None"
        q, k, v = _in_projection_packed(query, key, value, in_proj_weight, in_proj_bias)
    else:
        assert q_proj_weight is not None, "use_separate_proj_weight is True but q_proj_weight is None"
        assert k_proj_weight is not None, "use_separate_proj_weight is True but k_proj_weight is None"
        assert v_proj_weight is not None, "use_separate_proj_weight is True but v_proj_weight is None"
        if in_proj_bias is None:
            b_q = b_k = b_v = None
        else:
            b_q, b_k, b_v = in_proj_bias.chunk(3)
        q, k, v = _in_projection(query, key, value, q_proj_weight, k_proj_weight, v_proj_weight, b_q, b_k, b_v)

#     print('query_emb')
#     print(q)
#     print('key_emb')
#     print(k)
#     print('value_emb')
#     print(v)
    # prep attention mask
    if attn_mask is not None:
        if attn_mask.dtype == torch.uint8:
            warnings.warn("Byte tensor for attn_mask in nn.MultiheadAttention is deprecated. Use bool tensor instead.")
            attn_mask = attn_mask.to(torch.bool)
        else:
            assert attn_mask.is_floating_point() or attn_mask.dtype == torch.bool, \
                f"Only float, byte, and bool types are supported for attn_mask, not {attn_mask.dtype}"
        # ensure attn_mask's dim is 3
        if attn_mask.dim() == 2:
            correct_2d_size = (tgt_len, src_len)
            if attn_mask.shape != correct_2d_size:
                raise RuntimeError(f"The shape of the 2D attn_mask is {attn_mask.shape}, but should be {correct_2d_size}.")
            attn_mask = attn_mask.unsqueeze(0)
        elif attn_mask.dim() == 3:
            correct_3d_size = (bsz * num_heads, tgt_len, src_len)
            if attn_mask.shape != correct_3d_size:
                raise RuntimeError(f"The shape of the 3D attn_mask is {attn_mask.shape}, but should be {correct_3d_size}.")
        else:
            raise RuntimeError(f"attn_mask's dimension {attn_mask.dim()} is not supported")

    # prep key padding mask
    if key_padding_mask is not None and key_padding_mask.dtype == torch.uint8:
        warnings.warn("Byte tensor for key_padding_mask in nn.MultiheadAttention is deprecated. Use bool tensor instead.")
        key_padding_mask = key_padding_mask.to(torch.bool)

    # add bias along batch dimension (currently second)
    if bias_k is not None and bias_v is not None:
        assert static_k is None, "bias cannot be added to static key."
        assert static_v is None, "bias cannot be added to static value."
        k = torch.cat([k, bias_k.repeat(1, bsz, 1)])
        v = torch.cat([v, bias_v.repeat(1, bsz, 1)])
        if attn_mask is not None:
            attn_mask = pad(attn_mask, (0, 1))
        if key_padding_mask is not None:
            key_padding_mask = pad(key_padding_mask, (0, 1))
    else:
        assert bias_k is None
        assert bias_v is None

    #
    # reshape q, k, v for multihead attention and make em batch first
    #
    q = q.contiguous().view(tgt_len, bsz * num_heads, head_dim).transpose(0, 1)  
    if static_k is None:
        k = k.contiguous().view(k.shape[0], bsz * num_heads, head_dim).transpose(0, 1)
    else:
        # TODO finish disentangling control flow so we don't do in-projections when statics are passed
        assert static_k.size(0) == bsz * num_heads, \
            f"expecting static_k.size(0) of {bsz * num_heads}, but got {static_k.size(0)}"
        assert static_k.size(2) == head_dim, \
            f"expecting static_k.size(2) of {head_dim}, but got {static_k.size(2)}"
        k = static_k
    if static_v is None:
        v = v.contiguous().view(v.shape[0], bsz * num_heads, head_dim).transpose(0, 1)
    else:
        # TODO finish disentangling control flow so we don't do in-projections when statics are passed
        assert static_v.size(0) == bsz * num_heads, \
            f"expecting static_v.size(0) of {bsz * num_heads}, but got {static_v.size(0)}"
        assert static_v.size(2) == head_dim, \
            f"expecting static_v.size(2) of {head_dim}, but got {static_v.size(2)}"
        v = static_v

    # update source sequence length after adjustments
    src_len = k.size(1)

    # merge key padding and attention masks
    if key_padding_mask is not None:
        assert key_padding_mask.shape == (bsz, src_len), \
            f"expecting key_padding_mask shape of {(bsz, src_len)}, but got {key_padding_mask.shape}"
        key_padding_mask = key_padding_mask.view(bsz, 1, 1, src_len).   \
            expand(-1, num_heads, -1, -1).reshape(bsz * num_heads, 1, src_len)
        if attn_mask is None:
            attn_mask = key_padding_mask
        elif attn_mask.dtype == torch.bool:
            attn_mask = attn_mask.logical_or(key_padding_mask)
        else:
            attn_mask = attn_mask.masked_fill(key_padding_mask, float("-inf"))

    # convert mask to float
    if attn_mask is not None and attn_mask.dtype == torch.bool:
        new_attn_mask = torch.zeros_like(attn_mask, dtype=q.dtype)
        new_attn_mask.masked_fill_(attn_mask, float("-inf"))
        attn_mask = new_attn_mask

    # adjust dropout probability
    if not training:
        dropout_p = 0.0

    #
    # (deep breath) calculate attention and out projection
    #
    attn_output, attn_output_weights = _scaled_dot_product_attention(q, k, v, attn_mask, dropout_p)
    attn_output = attn_output.transpose(0, 1).contiguous().view(tgt_len * bsz, embed_dim)
    attn_output = F.linear(attn_output, out_proj_weight, out_proj_bias)
    attn_output = attn_output.view(tgt_len, bsz, attn_output.size(1))

    if need_weights:
        # optionally average attention weights over heads
        attn_output_weights = attn_output_weights.view(bsz, num_heads, tgt_len, src_len)
        if average_attn_weights:
            attn_output_weights = attn_output_weights.sum(dim=1) / num_heads

        if not is_batched:
            # squeeze the output if input was unbatched
            attn_output = attn_output.squeeze(1)
            attn_output_weights = attn_output_weights.squeeze(0)
        return attn_output, attn_output_weights
    else:
        if not is_batched:
            # squeeze the output if input was unbatched
            attn_output = attn_output.squeeze(1)
        return attn_output, None

In [7]:
class MultiheadAttention(nn.Module):
    r"""Allows the model to jointly attend to information
    from different representation subspaces as described in the paper:
    `Attention Is All You Need <https://arxiv.org/abs/1706.03762>`_.

    Multi-Head Attention is defined as:

    .. math::
        \text{MultiHead}(Q, K, V) = \text{Concat}(head_1,\dots,head_h)W^O

    where :math:`head_i = \text{Attention}(QW_i^Q, KW_i^K, VW_i^V)`.

    Args:
        embed_dim: Total dimension of the model.
        num_heads: Number of parallel attention heads. Note that ``embed_dim`` will be split
            across ``num_heads`` (i.e. each head will have dimension ``embed_dim // num_heads``).
        dropout: Dropout probability on ``attn_output_weights``. Default: ``0.0`` (no dropout).
        bias: If specified, adds bias to input / output projection layers. Default: ``True``.
        add_bias_kv: If specified, adds bias to the key and value sequences at dim=0. Default: ``False``.
        add_zero_attn: If specified, adds a new batch of zeros to the key and value sequences at dim=1.
            Default: ``False``.
        kdim: Total number of features for keys. Default: ``None`` (uses ``kdim=embed_dim``).
        vdim: Total number of features for values. Default: ``None`` (uses ``vdim=embed_dim``).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).

    Examples::

        >>> multihead_attn = nn.MultiheadAttention(embed_dim, num_heads)
        >>> attn_output, attn_output_weights = multihead_attn(query, key, value)
    """

    def __init__(self, embed_dim, num_heads, dropout=0., bias=True, add_bias_kv=False, add_zero_attn=False,
                 kdim=None, vdim=None, batch_first=False, device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(MultiheadAttention, self).__init__()
        self.embed_dim = embed_dim
        self.kdim = kdim if kdim is not None else embed_dim
        self.vdim = vdim if vdim is not None else embed_dim
        self._qkv_same_embed_dim = self.kdim == embed_dim and self.vdim == embed_dim

        self.num_heads = num_heads
        self.dropout = dropout
        self.batch_first = batch_first
        self.head_dim = embed_dim // num_heads
        assert self.head_dim * num_heads == self.embed_dim, "embed_dim must be divisible by num_heads"

        if self._qkv_same_embed_dim is False:
            self.q_proj_weight = Parameter(torch.empty((embed_dim, embed_dim), **factory_kwargs))
            self.k_proj_weight = Parameter(torch.empty((embed_dim, self.kdim), **factory_kwargs))
            self.v_proj_weight = Parameter(torch.empty((embed_dim, self.vdim), **factory_kwargs))
            self.register_parameter('in_proj_weight', None)
        else:
            self.in_proj_weight = Parameter(torch.empty((3 * embed_dim, embed_dim), **factory_kwargs))
            self.register_parameter('q_proj_weight', None)
            self.register_parameter('k_proj_weight', None)
            self.register_parameter('v_proj_weight', None)

        if bias:
            self.in_proj_bias = Parameter(torch.empty(3 * embed_dim, **factory_kwargs))
        else:
            self.register_parameter('in_proj_bias', None)
        self.out_proj = NonDynamicallyQuantizableLinear(embed_dim, embed_dim, bias=bias, **factory_kwargs)

        if add_bias_kv:
            self.bias_k = Parameter(torch.empty((1, 1, embed_dim), **factory_kwargs))
            self.bias_v = Parameter(torch.empty((1, 1, embed_dim), **factory_kwargs))
        else:
            self.bias_k = self.bias_v = None

        self.add_zero_attn = add_zero_attn

        self._reset_parameters()

    def _reset_parameters(self):
        if self._qkv_same_embed_dim:
            xavier_uniform_(self.in_proj_weight)
        else:
            xavier_uniform_(self.q_proj_weight)
            xavier_uniform_(self.k_proj_weight)
            xavier_uniform_(self.v_proj_weight)

        if self.in_proj_bias is not None:
            constant_(self.in_proj_bias, 0.)
            constant_(self.out_proj.bias, 0.)
        if self.bias_k is not None:
            xavier_normal_(self.bias_k)
        if self.bias_v is not None:
            xavier_normal_(self.bias_v)

    def __setstate__(self, state):
        # Support loading old MultiheadAttention checkpoints generated by v1.1.0
        if '_qkv_same_embed_dim' not in state:
            state['_qkv_same_embed_dim'] = True

        super(MultiheadAttention, self).__setstate__(state)

    def forward(self, query: Tensor, key: Tensor, value: Tensor, key_padding_mask: Optional[Tensor] = None,
                need_weights: bool = True, attn_mask: Optional[Tensor] = None,
                average_attn_weights: bool = True) -> Tuple[Tensor, Optional[Tensor]]:
        r"""
    Args:
        query: Query embeddings of shape :math:`(L, E_q)` for unbatched input, :math:`(L, N, E_q)` when ``batch_first=False``
            or :math:`(N, L, E_q)` when ``batch_first=True``, where :math:`L` is the target sequence length,
            :math:`N` is the batch size, and :math:`E_q` is the query embedding dimension ``embed_dim``.
            Queries are compared against key-value pairs to produce the output.
            See "Attention Is All You Need" for more details.
        key: Key embeddings of shape :math:`(S, E_k)` for unbatched input, :math:`(S, N, E_k)` when ``batch_first=False``
            or :math:`(N, S, E_k)` when ``batch_first=True``, where :math:`S` is the source sequence length,
            :math:`N` is the batch size, and :math:`E_k` is the key embedding dimension ``kdim``.
            See "Attention Is All You Need" for more details.
        value: Value embeddings of shape :math:`(S, E_v)` for unbatched input, :math:`(S, N, E_v)` when
            ``batch_first=False`` or :math:`(N, S, E_v)` when ``batch_first=True``, where :math:`S` is the source
            sequence length, :math:`N` is the batch size, and :math:`E_v` is the value embedding dimension ``vdim``.
            See "Attention Is All You Need" for more details.
        key_padding_mask: If specified, a mask of shape :math:`(N, S)` indicating which elements within ``key``
            to ignore for the purpose of attention (i.e. treat as "padding"). For unbatched `query`, shape should be :math:`(S)`.
            Binary and byte masks are supported.
            For a binary mask, a ``True`` value indicates that the corresponding ``key`` value will be ignored for
            the purpose of attention. For a byte mask, a non-zero value indicates that the corresponding ``key``
            value will be ignored.
        need_weights: If specified, returns ``attn_output_weights`` in addition to ``attn_outputs``.
            Default: ``True``.
        attn_mask: If specified, a 2D or 3D mask preventing attention to certain positions. Must be of shape
            :math:`(L, S)` or :math:`(N\cdot\text{num\_heads}, L, S)`, where :math:`N` is the batch size,
            :math:`L` is the target sequence length, and :math:`S` is the source sequence length. A 2D mask will be
            broadcasted across the batch while a 3D mask allows for a different mask for each entry in the batch.
            Binary, byte, and float masks are supported. For a binary mask, a ``True`` value indicates that the
            corresponding position is not allowed to attend. For a byte mask, a non-zero value indicates that the
            corresponding position is not allowed to attend. For a float mask, the mask values will be added to
            the attention weight.
        average_attn_weights: If true, indicates that the returned ``attn_weights`` should be averaged across
            heads. Otherwise, ``attn_weights`` are provided separately per head. Note that this flag only has an
            effect when ``need_weights=True.``. Default: True (i.e. average weights across heads)

    Outputs:
        - **attn_output** - Attention outputs of shape :math:`(L, E)` when input is unbatched,
          :math:`(L, N, E)` when ``batch_first=False`` or :math:`(N, L, E)` when ``batch_first=True``,
          where :math:`L` is the target sequence length, :math:`N` is the batch size, and :math:`E` is the
          embedding dimension ``embed_dim``.
        - **attn_output_weights** - Only returned when ``need_weights=True``. If ``average_attn_weights=True``,
          returns attention weights averaged across heads of shape :math:`(L, S)` when input is unbatched or
          :math:`(N, L, S)`, where :math:`N` is the batch size, :math:`L` is the target sequence length, and
          :math:`S` is the source sequence length. If ``average_weights=False``, returns attention weights per
          head of shape :math:`(num_heads, L, S)` when input is unbatched or :math:`(N, num_heads, L, S)`.

        .. note::
            `batch_first` argument is ignored for unbatched inputs.
        """
        
        is_batched = query.dim() == 3
        if self.batch_first and is_batched:
            query, key, value = [x.transpose(1, 0) for x in (query, key, value)]

        if not self._qkv_same_embed_dim:
            attn_output, attn_output_weights = multi_head_attention_forward(
                query, key, value, self.embed_dim, self.num_heads,
                self.in_proj_weight, self.in_proj_bias,
                self.bias_k, self.bias_v, self.add_zero_attn,
                self.dropout, self.out_proj.weight, self.out_proj.bias,
                training=self.training,
                key_padding_mask=key_padding_mask, need_weights=need_weights,
                attn_mask=attn_mask, use_separate_proj_weight=True,
                q_proj_weight=self.q_proj_weight, k_proj_weight=self.k_proj_weight,
                v_proj_weight=self.v_proj_weight, average_attn_weights=average_attn_weights)
        else:
            attn_output, attn_output_weights = multi_head_attention_forward(
                query, key, value, self.embed_dim, self.num_heads,
                self.in_proj_weight, self.in_proj_bias,
                self.bias_k, self.bias_v, self.add_zero_attn,
                self.dropout, self.out_proj.weight, self.out_proj.bias,
                training=self.training,
                key_padding_mask=key_padding_mask, need_weights=need_weights,
                attn_mask=attn_mask, average_attn_weights=average_attn_weights)
        if self.batch_first and is_batched:
            return attn_output.transpose(1, 0), attn_output_weights
        else:
            return attn_output, attn_output_weights
        


In [8]:
def _get_clones(module, N):
    return ModuleList([copy.deepcopy(module) for i in range(N)])



class TransformerModel(Module):
    r"""A transformer model. User is able to modify the attributes as needed. The architecture
    is based on the paper "Attention Is All You Need". Ashish Vaswani, Noam Shazeer,
    Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez, Lukasz Kaiser, and
    Illia Polosukhin. 2017. Attention is all you need. In Advances in Neural Information
    Processing Systems, pages 6000-6010.
    Args:
        d_model: the number of expected features in the encoder/decoder inputs (default=512).
        nhead: the number of heads in the multiheadattention models (default=8).
        num_encoder_layers: the number of sub-encoder-layers in the encoder (default=6).
        num_decoder_layers: the number of sub-decoder-layers in the decoder (default=6).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of encoder/decoder intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        custom_encoder: custom encoder (default=None).
        custom_decoder: custom decoder (default=None).
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, encoder and decoder layers will perform LayerNorms before
            other attention and feedforward operations, otherwise after. Default: ``False`` (after).
    Examples::
        >>> transformer_model = nn.Transformer(nhead=16, num_encoder_layers=12)
        >>> src = torch.rand((10, 32, 512))
        >>> tgt = torch.rand((20, 32, 512))
        >>> out = transformer_model(src, tgt)
    Note: A full example to apply nn.Transformer module for the word language model is available in
    https://github.com/pytorch/examples/tree/master/word_language_model
    """

    def __init__(self, d_model: int = 512, nhead: int = 8, num_encoder_layers: int = 6,
                 num_decoder_layers: int = 6, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 custom_encoder: Optional[Any] = None, custom_decoder: Optional[Any] = None,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerModel, self).__init__()

        if custom_encoder is not None:
            self.encoder = custom_encoder
        else:
            encoder_layer = TransformerEncoderLayer(d_model, nhead, dim_feedforward, dropout,
                                                    activation, layer_norm_eps, batch_first, norm_first, 
                                                    use_norm,
                                                    **factory_kwargs)
            encoder_norm = None
            if use_norm:
                encoder_norm = LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
            self.encoder = TransformerEncoder(encoder_layer, num_encoder_layers, encoder_norm)

        if custom_decoder is not None:
            self.decoder = custom_decoder
        else:
            decoder_layer = TransformerDecoderLayer(d_model, nhead, dim_feedforward, dropout,
                                                    activation, layer_norm_eps, batch_first, norm_first,
                                                    use_norm,
                                                    **factory_kwargs)
            decoder_norm = None
            if use_norm:
                decoder_norm = LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
            self.decoder = TransformerDecoder(decoder_layer, num_decoder_layers, decoder_norm)

        self._reset_parameters()

        self.d_model = d_model
        self.nhead = nhead

        self.batch_first = batch_first

    def forward(self, src: Tensor, tgt: Tensor, src_mask: Optional[Tensor] = None, tgt_mask: Optional[Tensor] = None,
                memory_mask: Optional[Tensor] = None, src_key_padding_mask: Optional[Tensor] = None,
                tgt_key_padding_mask: Optional[Tensor] = None, memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Take in and process masked source/target sequences.
        Args:
            src: the sequence to the encoder (required).
            tgt: the sequence to the decoder (required).
            src_mask: the additive mask for the src sequence (optional).
            tgt_mask: the additive mask for the tgt sequence (optional).
            memory_mask: the additive mask for the encoder output (optional).
            src_key_padding_mask: the ByteTensor mask for src keys per batch (optional).
            tgt_key_padding_mask: the ByteTensor mask for tgt keys per batch (optional).
            memory_key_padding_mask: the ByteTensor mask for memory keys per batch (optional).
        Shape:
            - src: :math:`(S, E)` for unbatched input, :math:`(S, N, E)` if `batch_first=False` or
              `(N, S, E)` if `batch_first=True`.
            - tgt: :math:`(T, E)` for unbatched input, :math:`(T, N, E)` if `batch_first=False` or
              `(N, T, E)` if `batch_first=True`.
            - src_mask: :math:`(S, S)` or :math:`(N\cdot\text{num\_heads}, S, S)`.
            - tgt_mask: :math:`(T, T)` or :math:`(N\cdot\text{num\_heads}, T, T)`.
            - memory_mask: :math:`(T, S)`.
            - src_key_padding_mask: :math:`(S)` for unbatched input otherwise :math:`(N, S)`.
            - tgt_key_padding_mask: :math:`(T)` for unbatched input otherwise :math:`(N, T)`.
            - memory_key_padding_mask: :math:`(S)` for unbatched input otherwise :math:`(N, S)`.
            Note: [src/tgt/memory]_mask ensures that position i is allowed to attend the unmasked
            positions. If a ByteTensor is provided, the non-zero positions are not allowed to attend
            while the zero positions will be unchanged. If a BoolTensor is provided, positions with ``True``
            are not allowed to attend while ``False`` values will be unchanged. If a FloatTensor
            is provided, it will be added to the attention weight.
            [src/tgt/memory]_key_padding_mask provides specified elements in the key to be ignored by
            the attention. If a ByteTensor is provided, the non-zero positions will be ignored while the zero
            positions will be unchanged. If a BoolTensor is provided, the positions with the
            value of ``True`` will be ignored while the position with the value of ``False`` will be unchanged.
            - output: :math:`(T, E)` for unbatched input, :math:`(T, N, E)` if `batch_first=False` or
              `(N, T, E)` if `batch_first=True`.
            Note: Due to the multi-head attention architecture in the transformer model,
            the output sequence length of a transformer is same as the input sequence
            (i.e. target) length of the decoder.
            where S is the source sequence length, T is the target sequence length, N is the
            batch size, E is the feature number
        Examples:
            >>> output = transformer_model(src, tgt, src_mask=src_mask, tgt_mask=tgt_mask)
        """

        is_batched = src.dim() == 3
        if not self.batch_first and src.size(1) != tgt.size(1) and is_batched:
            raise RuntimeError("the batch number of src and tgt must be equal")
        elif self.batch_first and src.size(0) != tgt.size(0) and is_batched:
            raise RuntimeError("the batch number of src and tgt must be equal")

        if src.size(-1) != self.d_model or tgt.size(-1) != self.d_model:
            raise RuntimeError("the feature number of src and tgt must be equal to d_model")
        
#         print('ENCODER_STEP')
        memory = self.encoder(src, mask=src_mask, src_key_padding_mask=src_key_padding_mask)
#         print('DECODER_STEP')
        output = self.decoder(tgt, memory, tgt_mask=tgt_mask, memory_mask=memory_mask,
                              tgt_key_padding_mask=tgt_key_padding_mask,
                              memory_key_padding_mask=memory_key_padding_mask)
        return output

    @staticmethod
    def generate_square_subsequent_mask(sz: int) -> Tensor:
        r"""Generate a square mask for the sequence. The masked positions are filled with float('-inf').
            Unmasked positions are filled with float(0.0).
        """
        return torch.triu(torch.full((sz, sz), float('-inf')), diagonal=1)

    def _reset_parameters(self):
        r"""Initiate parameters in the transformer model."""

        for p in self.parameters():
            if p.dim() > 1:
                xavier_uniform_(p)


class TransformerEncoder(Module):
    r"""TransformerEncoder is a stack of N encoder layers. Users can build the
    BERT(https://arxiv.org/abs/1810.04805) model with corresponding parameters.
    Args:
        encoder_layer: an instance of the TransformerEncoderLayer() class (required).
        num_layers: the number of sub-encoder-layers in the encoder (required).
        norm: the layer normalization component (optional).
        enable_nested_tensor: if True, input will automatically convert to nested tensor
            (and convert back on output). This will improve the overall performance of
            TransformerEncoder when padding rate is high. Default: ``True`` (enabled).
    Examples::
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8)
        >>> transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=6)
        >>> src = torch.rand(10, 32, 512)
        >>> out = transformer_encoder(src)
    """
    __constants__ = ['norm']

    def __init__(self, encoder_layer, num_layers, norm=None, enable_nested_tensor=True):
        super(TransformerEncoder, self).__init__()
        self.layers = _get_clones(encoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm
        self.enable_nested_tensor = enable_nested_tensor

    def forward(self, src: Tensor, mask: Optional[Tensor] = None, src_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the input through the encoder layers in turn.
        Args:
            src: the sequence to the encoder (required).
            mask: the mask for the src sequence (optional).
            src_key_padding_mask: the mask for the src keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        for mod in self.layers:
            output = mod(src, src_mask=mask, src_key_padding_mask=src_key_padding_mask)

        if self.norm is not None:
            output = self.norm(output)

        return output


class TransformerDecoder(Module):
    r"""TransformerDecoder is a stack of N decoder layers
    Args:
        decoder_layer: an instance of the TransformerDecoderLayer() class (required).
        num_layers: the number of sub-decoder-layers in the decoder (required).
        norm: the layer normalization component (optional).
    Examples::
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8)
        >>> transformer_decoder = nn.TransformerDecoder(decoder_layer, num_layers=6)
        >>> memory = torch.rand(10, 32, 512)
        >>> tgt = torch.rand(20, 32, 512)
        >>> out = transformer_decoder(tgt, memory)
    """
    __constants__ = ['norm']

    def __init__(self, decoder_layer, num_layers, norm=None):
        super(TransformerDecoder, self).__init__()
        self.layers = _get_clones(decoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm

    def forward(self, tgt: Tensor, memory: Tensor, tgt_mask: Optional[Tensor] = None,
                memory_mask: Optional[Tensor] = None, tgt_key_padding_mask: Optional[Tensor] = None,
                memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the inputs (and mask) through the decoder layer in turn.
        Args:
            tgt: the sequence to the decoder (required).
            memory: the sequence from the last layer of the encoder (required).
            tgt_mask: the mask for the tgt sequence (optional).
            memory_mask: the mask for the memory sequence (optional).
            tgt_key_padding_mask: the mask for the tgt keys per batch (optional).
            memory_key_padding_mask: the mask for the memory keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        output = tgt
#         print('x before decoder')
#         print(output)
        for mod in self.layers:
            output = mod(output, memory, tgt_mask=tgt_mask,
                         memory_mask=memory_mask,
                         tgt_key_padding_mask=tgt_key_padding_mask,
                         memory_key_padding_mask=memory_key_padding_mask)

        if self.norm is not None:
            output = self.norm(output)

        return output

class TransformerEncoderLayer(Module):
    r"""TransformerEncoderLayer is made up of self-attn and feedforward network.
    This standard encoder layer is based on the paper "Attention Is All You Need".
    Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez,
    Lukasz Kaiser, and Illia Polosukhin. 2017. Attention is all you need. In Advances in
    Neural Information Processing Systems, pages 6000-6010. Users may modify or implement
    in a different way during application.
    Args:
        d_model: the number of expected features in the input (required).
        nhead: the number of heads in the multiheadattention models (required).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of the intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, layer norm is done prior to attention and feedforward
            operations, respectivaly. Otherwise it's done after. Default: ``False`` (after).
    Examples::
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8)
        >>> src = torch.rand(10, 32, 512)
        >>> out = encoder_layer(src)
    Alternatively, when ``batch_first`` is ``True``:
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8, batch_first=True)
        >>> src = torch.rand(32, 10, 512)
        >>> out = encoder_layer(src)
    Fast path:
        forward() will use a special optimized implementation if all of the following
        conditions are met:
        - Either autograd is disabled (using ``torch.inference_mode`` or ``torch.no_grad``) or no tensor
          argument ``requires_grad``
        - training is disabled (using ``.eval()``)
        - batch_first is ``True`` and the input is batched (i.e., ``src.dim() == 3``)
        - norm_first is ``False`` (this restriction may be loosened in the future)
        - activation is one of: ``"relu"``, ``"gelu"``, ``torch.functional.relu``, or ``torch.functional.gelu``
        - at most one of ``src_mask`` and ``src_key_padding_mask`` is passed
        - if src is a `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_, neither ``src_mask``
          nor ``src_key_padding_mask`` is passed
        - the two ``LayerNorm`` instances have a consistent ``eps`` value (this will naturally be the case
          unless the caller has manually modified one without modifying the other)
        If the optimized implementation is in use, a
        `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_ can be
        passed for ``src`` to represent padding more efficiently than using a padding
        mask. In this case, a `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_ will be
        returned, and an additional speedup proportional to the fraction of the input that
        is padding can be expected.
    """
    __constants__ = ['batch_first', 'norm_first']

    def __init__(self, d_model: int, nhead: int, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerEncoderLayer, self).__init__()
        self.self_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                            **factory_kwargs)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward, **factory_kwargs)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model, **factory_kwargs)

        self.norm_first = norm_first
        self.norm1 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm2 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)

        
        self.activation = activation
        
        self.use_norm = use_norm

    def __setstate__(self, state):
        if 'activation' not in state:
            state['activation'] = F.relu
        super(TransformerEncoderLayer, self).__setstate__(state)

    def forward(self, src: Tensor, src_mask: Optional[Tensor] = None,
                src_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the input through the encoder layer.
        Args:
            src: the sequence to the encoder layer (required).
            src_mask: the mask for the src sequence (optional).
            src_key_padding_mask: the mask for the src keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """

        # see Fig. 1 of https://arxiv.org/pdf/2002.04745v1.pdf

    
        x = src
        if self.norm_first:
            x = x + self._sa_block(self.norm1(x), src_mask, src_key_padding_mask)
            x = x + self._ff_block(self.norm2(x))
        else:
            x = x + self._sa_block(x, src_mask, src_key_padding_mask)
            if self.use_norm:
                x = self.norm1(x)
#             print('x after self attn, res, norm')
#             print(x)
            x = x + self._ff_block(x)
            if self.use_norm:
                x = self.norm2(x)
            

        return x

    # self-attention block
    def _sa_block(self, x: Tensor,
                  attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.self_attn(x, x, x,
                           attn_mask=attn_mask,
                           key_padding_mask=key_padding_mask,
                           need_weights=False)[0]
        return self.dropout1(x)

    # feed forward block
    def _ff_block(self, x: Tensor) -> Tensor:
        x = self.linear2(self.dropout(self.activation(self.linear1(x))))
        return self.dropout2(x)


class TransformerDecoderLayer(Module):
    r"""TransformerDecoderLayer is made up of self-attn, multi-head-attn and feedforward network.
    This standard decoder layer is based on the paper "Attention Is All You Need".
    Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez,
    Lukasz Kaiser, and Illia Polosukhin. 2017. Attention is all you need. In Advances in
    Neural Information Processing Systems, pages 6000-6010. Users may modify or implement
    in a different way during application.
    Args:
        d_model: the number of expected features in the input (required).
        nhead: the number of heads in the multiheadattention models (required).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of the intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, layer norm is done prior to self attention, multihead
            attention and feedforward operations, respectivaly. Otherwise it's done after.
            Default: ``False`` (after).
    Examples::
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8)
        >>> memory = torch.rand(10, 32, 512)
        >>> tgt = torch.rand(20, 32, 512)
        >>> out = decoder_layer(tgt, memory)
    Alternatively, when ``batch_first`` is ``True``:
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8, batch_first=True)
        >>> memory = torch.rand(32, 10, 512)
        >>> tgt = torch.rand(32, 20, 512)
        >>> out = decoder_layer(tgt, memory)
    """
    __constants__ = ['batch_first', 'norm_first']

    def __init__(self, d_model: int, nhead: int, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerDecoderLayer, self).__init__()
        self.self_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                            **factory_kwargs)
        self.multihead_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                                 **factory_kwargs)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward, **factory_kwargs)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model, **factory_kwargs)

        self.norm_first = norm_first
        self.norm1 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm2 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm3 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)
        self.dropout3 = nn.Dropout(dropout)

        self.activation = activation
        
        self.use_norm = use_norm

    def __setstate__(self, state):
        if 'activation' not in state:
            state['activation'] = F.relu
        super(TransformerDecoderLayer, self).__setstate__(state)

    def forward(self, tgt: Tensor, memory: Tensor, tgt_mask: Optional[Tensor] = None, memory_mask: Optional[Tensor] = None,
                tgt_key_padding_mask: Optional[Tensor] = None, memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the inputs (and mask) through the decoder layer.
        Args:
            tgt: the sequence to the decoder layer (required).
            memory: the sequence from the last layer of the encoder (required).
            tgt_mask: the mask for the tgt sequence (optional).
            memory_mask: the mask for the memory sequence (optional).
            tgt_key_padding_mask: the mask for the tgt keys per batch (optional).
            memory_key_padding_mask: the mask for the memory keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        # see Fig. 1 of https://arxiv.org/pdf/2002.04745v1.pdf

        x = tgt
        if self.norm_first:
            
            x = x + self._sa_block(self.norm1(x), tgt_mask, tgt_key_padding_mask) 
            
            
            x = x + self._mha_block(self.norm2(x), memory, memory_mask, memory_key_padding_mask)  
            
            x = x + self._ff_block(self.norm3(x))
        else:

            x = x + self._sa_block(x, tgt_mask, tgt_key_padding_mask)
            if self.use_norm:
                x = self.norm1(x)
                
#             print('x after self attn, res, norm')
#             print(x)
             
            x = x + self._mha_block(x, memory, memory_mask, memory_key_padding_mask)
            if self.use_norm:
                x = self.norm2(x)
                
            x = x + self._ff_block(x)
            if self.use_norm:
                x = self.norm3(x)
            
#         print('declayer out')
#         print(x)
        return x

    # self-attention block
    def _sa_block(self, x: Tensor,
                  attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.self_attn(x, x, x,
                               attn_mask=attn_mask,
                               key_padding_mask=key_padding_mask,
                               need_weights=False)[0]
        return self.dropout1(x)

    # multihead attention block
    def _mha_block(self, x: Tensor, mem: Tensor,
                   attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.multihead_attn(x, mem, mem,
                                attn_mask=attn_mask,
                                key_padding_mask=key_padding_mask,
                                need_weights=False)[0]
        return self.dropout2(x)

    # feed forward block
    def _ff_block(self, x: Tensor) -> Tensor:
        x = self.linear2(self.dropout(self.activation(self.linear1(x))))
        return self.dropout3(x)

In [9]:
# from https://pytorch.org/tutorials/beginner/transformer_tutorial.html

class PositionalEncoding(nn.Module):

    def __init__(self, d_model: int, dropout: float = 0.1, max_len: int = 5000):
        super().__init__()
        self.dropout = nn.Dropout(p=dropout)

        position = torch.arange(max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2) * (-math.log(10000.0) / d_model))
        pe = torch.zeros(max_len, 1, d_model)
        pe[:, 0, 0::2] = torch.sin(position * div_term)
        pe[:, 0, 1::2] = torch.cos(position * div_term)
        self.register_buffer('pe', pe)

    def forward(self, x: Tensor) -> Tensor:
        """
        Args:
            x: Tensor, shape [seq_len, batch_size, embedding_dim]
        """
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

In [10]:
class Transformer(Module):
    
    
    def __init__(self, d_model=64, nhead=4, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=512, dropout=0.1, activation=F.gelu, use_norm=False):
        
        super(Transformer, self).__init__()
        self.transformer_model = TransformerModel(d_model=d_model, nhead=nhead, num_encoder_layers=num_encoder_layers,
                                                  num_decoder_layers=num_decoder_layers, dim_feedforward=dim_feedforward,
                                                  dropout=dropout, activation=activation, use_norm=use_norm)
        
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        self.input_projection1 = nn.Linear(1, d_model)
        self.input_projection2 = nn.Linear(d_model, d_model)
        self.output_projection = nn.Linear(d_model, 1)
        
    def forward(self, encoder_x, decoder_x, src_mask=None, tgt_mask=None, memory_mask=None):
        """ encoder_x should be vector of size input_seq_len x bs x 1   
            decoder_x should be vector of size output_seq_len x bs x 1
        """

        
        encoder_x = self.pos_encoder(self.input_projection2(torch.sigmoid(self.input_projection1(encoder_x))))
        decoder_x = self.pos_encoder(self.input_projection2(torch.sigmoid(self.input_projection1(decoder_x))))
        

        x = self.transformer_model(encoder_x, decoder_x, 
                                   src_mask=src_mask, tgt_mask=tgt_mask, memory_mask=memory_mask)
        x = self.output_projection(x)
        return x

    
        
        
        

In [ ]:
# process data for vanilla transformer. I.e. create all possible sequences. Include null values

In [ ]:
series_values = data[0]['series_value']
series_values

In [ ]:
date_range = pd.date_range(start='1996-03-18', periods=791, freq='D')  # can do this because all series have same length
date_range

In [ ]:
# to make it easy, set a default encoder and decoder seq len
encoder_seq_len = 14  # i.e. 2 weeks of data to use in encoder
decoder_seq_len = 7

In [ ]:
# think about rolling cross validation but for now just have one test set at the end
train_set_dates = date_range[date_range < '1998-01-01'] 
test_set_dates = date_range[date_range >= datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') - datetime.timedelta(encoder_seq_len)] 
# i.e. the first dates we want to predict are the week starting from 1998-01-01
# have to make sure these values we want to predict never pop up in the training set, including the decoder inputs
# in other words the latest decoder output should be one day before 1998-01-01 to avoid any leakage


In [11]:
def split_data_into_sequences(data_series, encoder_seq_len, decoder_seq_len, start_date=None, end_date=None, 
                              absolute_start_date='1996-03-18'):
    
    data_series = list(pd.Series(data_series).replace('NaN', np.nan))
    date_range = pd.date_range(start=absolute_start_date, periods=len(data_series), freq='D')
    start_date_idx = date_range.get_loc(start_date) if start_date is not None else 0
    end_date_idx = date_range.get_loc(end_date) if end_date is not None else len(date_range) - 1   

    data_subset = torch.Tensor(data_series[start_date_idx : end_date_idx + 1])
    
    
    sequences_ = []
    for start in range(0, len(data_subset) - decoder_seq_len - encoder_seq_len):
        enc_seq = data_subset[start : start + encoder_seq_len]
        dec_seq = data_subset[start + encoder_seq_len - 1 : start + encoder_seq_len + decoder_seq_len - 1]
        ground_truth = data_subset[start + encoder_seq_len : start + encoder_seq_len + decoder_seq_len]
        if torch.sum(~torch.isnan(ground_truth)).item() > 0:  # sequences with all null ground truth exist. Exclude these model ruiners
            sequences_.append((enc_seq, dec_seq, ground_truth))
            
        
    
#     sequences_ = [(data_subset[start : start + encoder_seq_len],
#                    data_subset[start + encoder_seq_len - 1 : start + encoder_seq_len + decoder_seq_len - 1],
#                    data_subset[start + encoder_seq_len : start + encoder_seq_len + decoder_seq_len])
#                  for start in range(0, len(data_subset) - decoder_seq_len - encoder_seq_len)]
    
    return sequences_


def split_dataset_into_sequences(dataset, encoder_seq_len, decoder_seq_len, start_date=None, end_date=None, 
                                 absolute_start_date='1996-03-18'):
    all_sequences = []
    for time_series in dataset:
        sequences_ = split_data_into_sequences(time_series, encoder_seq_len, decoder_seq_len, start_date=start_date, 
                                               end_date=end_date, absolute_start_date=absolute_start_date)
        all_sequences.extend(sequences_)
    return all_sequences


In [12]:
encoder_seq_len = 14
decoder_seq_len = 7

In [90]:
torch.sum(~torch.isnan(torch.Tensor([np.nan, np.nan, np.nan]))).item() > 0

False

In [27]:
testing_start_date = datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') 
val_start_date = testing_start_date - datetime.timedelta(days=30*4)
training_end_date = val_start_date - datetime.timedelta(days=1)
val_end_date = testing_start_date - datetime.timedelta(days=1)

In [28]:
train_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, end_date=training_end_date)

In [ ]:
len(train_sequences)

In [ ]:
val_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, 
                                             start_date=val_start_date, end_date=val_end_date)

In [ ]:
len(val_sequences)

In [ ]:
test_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, start_date=testing_start_date)

In [ ]:
len(test_sequences)

In [ ]:
t = torch.Tensor([1, 2, 3])
i = torch.Tensor([0, np.nan, 1]).isnan().nonzero().squeeze()
torch.cat([t[:i], t[i+1:]])

In [ ]:
torch.Tensor([1]).reshape((1))

In [13]:
def create_null_masks_general(in_seq, out_seq, is_self_attn=True, seq_len_dim=0):
    in_seq_len = in_seq.shape[seq_len_dim]
    out_seq_len = out_seq.shape[seq_len_dim]
    isnan_res = in_seq.isnan().nonzero()
    if len(isnan_res) == 0:
        return torch.zeros((out_seq_len, in_seq_len))
    else:
        null_indices = isnan_res.squeeze()
        if isnan_res.shape[0] == 1:
            null_indices = null_indices.reshape((1,))
        mask = torch.zeros((out_seq_len, in_seq_len)).index_fill_(1, null_indices, float('-inf'))
        if is_self_attn:
            for index in null_indices:
                mask[index, index] = 0  # need this to prevent bug when null is in first position (of decoder self attn)
        return mask
    

In [14]:
def create_null_masks(enc_seq, dec_seq, seq_len_dim=0):
    enc_sa_null_mask = create_null_masks_general(enc_seq, enc_seq, seq_len_dim=seq_len_dim)
    dec_sa_null_mask = create_null_masks_general(dec_seq, dec_seq, seq_len_dim=seq_len_dim)
    dec_enc_null_mask = create_null_masks_general(enc_seq, dec_seq, is_self_attn=False, seq_len_dim=seq_len_dim)
    
    return enc_sa_null_mask, dec_sa_null_mask, dec_enc_null_mask

In [25]:
def create_sa_causality_mask(n_t):
    return TransformerModel.generate_square_subsequent_mask(n_t)

In [26]:
def generate_transformer_masks(encoder_seq, decoder_seq, encoder_causality=False, seq_length_dim=0):
    encoder_sa_null_mask, decoder_sa_null_mask, decoder_encoder_null_mask = create_null_masks(encoder_seq, decoder_seq, 
                                                                                              seq_length_dim)
    decoder_sa_causality_mask = create_sa_causality_mask(decoder_seq.shape[seq_length_dim])
    decoder_sa_mask = decoder_sa_null_mask + decoder_sa_causality_mask
    
    encoder_sa_mask = encoder_sa_null_mask
    if encoder_causality:
        encoder_sa_causality_mask = create_sa_causality_mask(encoder_seq.shape[seq_length_dim])
        encoder_sa_mask = encoder_sa_mask + encoder_sa_causality_mask
    
    return encoder_sa_mask, decoder_sa_mask, decoder_encoder_null_mask

In [33]:
# testing mask generation
enc_seq_ex, dec_seq_ex, _ = train_sequences[5]
print(enc_seq_ex)
print(dec_seq_ex)
generate_transformer_masks(enc_seq_ex, dec_seq_ex, encoder_causality=True)

tensor([16.6100, 15.3203, 11.6071, 19.8838, 23.7670, 34.0278, 33.7868, 18.2540,
        19.3878, 17.2619, 23.8095, 36.1253, 33.6026, 32.6247])
tensor([32.6247,  7.4830,     nan, 10.1332, 17.9138, 22.1230, 33.2341])


(tensor([[0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., -inf, -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., -inf, -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., -inf, -inf, -inf],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., -inf, -inf],
         [0., 0.

In [34]:
class SequenceDatasetForTransformer(Dataset):
    def __init__(self, sequences, encoder_causality=False):
        
        """ sequences should be list of tuples of len 3. 
        First item of a tuple: context (encoder input)
        Second item of a tuple: decoder input
        Third item of tuple: ground truth
        """
        self.sequences = sequences
        self.encoder_causality = encoder_causality
        
    def __len__(self):
        return len(self.sequences)
    
    def __getitem__(self, idx):
        encoder_input, decoder_input, ground_truth = self.sequences[idx]
        
        encoder_sa_mask, decoder_sa_mask, \
            decoder_encoder_null_mask = generate_transformer_masks(encoder_input, decoder_input, 
                                                                   encoder_causality=self.encoder_causality, 
                                                                   seq_length_dim=0)
        ground_truth_null_nans =  ground_truth.isnan().nonzero()
        ground_truth_null_indices = torch.ones(ground_truth.shape)
        null_indices_for_sequence = ground_truth_null_nans[:, 0]
        ground_truth_null_indices[null_indices_for_sequence] = 0
        
        encoder_input = torch.nan_to_num(encoder_input)
        decoder_input = torch.nan_to_num(decoder_input)
        ground_truth = torch.nan_to_num(ground_truth)
        
        return (encoder_input, decoder_input, ground_truth, ground_truth_null_indices,
                encoder_sa_mask, decoder_sa_mask, decoder_encoder_null_mask)
    

In [18]:
class SequenceDatasetForTransformerTesting(Dataset):
    def __init__(self, sequences):
        
        """ sequences should be list of tuples of len 3. 
        First item of a tuple: context (encoder input)
        Second item of a tuple: decoder input
        Third item of tuple: ground truth
        """
        self.sequences = sequences
        
    def __len__(self):
        return len(self.sequences)
    
    def __getitem__(self, idx):
        encoder_input, _, ground_truth = self.sequences[idx]
        
        ground_truth_null_nans =  ground_truth.isnan().nonzero()
        ground_truth_null_indices = torch.ones(ground_truth.shape)
        null_indices_for_sequence = ground_truth_null_nans[:, 0]
        ground_truth_null_indices[null_indices_for_sequence] = 0
        
        
        
        return (encoder_input, ground_truth, ground_truth_null_indices)

In [16]:
# def process_batch_nulls(encoder_input, decoder_input, ground_truth):  
#     # need this because null indices for ground truth will be different sizes
#     encoder_input = torch.nan_to_num(encoder_input)
#     decoder_input = torch.nan_to_num(decoder_input)
#     ground_truth_null_nans =  ground_truth.isnan().nonzero().T
#     ground_truth_null_indices = torch.ones(ground_truth.shape)  # need this to remove null elements in gt from loss
#     batch_size = ground_truth.shape[0]
    
#     for b in range(batch_size):
#         null_indices_for_sequence = ground_truth_null_nans[1][ground_truth_null_nans[0] == b]
#         ground_truth_null_indices[b, null_indices_for_sequence] = 0
        
#     ground_truth = torch.nan_to_num(ground_truth)
    
#     return encoder_input, decoder_input, ground_truth, ground_truth_null_indices

In [35]:
def format_input(encoder_input, decoder_input, encoder_sa_mask, decoder_sa_mask, decoder_encoder_null_mask, n_heads):
    encoder_sa_mask = encoder_sa_mask.repeat(n_heads, 1, 1)
    decoder_sa_mask = decoder_sa_mask.repeat(n_heads, 1, 1)
    decoder_encoder_null_mask = decoder_encoder_null_mask.repeat(n_heads, 1, 1)
    
    # need e, d to be of shape Length x bs x 1
    encoder_input = encoder_input.T.unsqueeze(-1)
    decoder_input = decoder_input.T.unsqueeze(-1)
    
    return encoder_input, decoder_input, encoder_sa_mask, decoder_sa_mask, decoder_encoder_null_mask

In [20]:
def create_train_val_test_sets(data, training_end_date, val_start_date, val_end_date, testing_start_date,
                              encoder_seq_len, decoder_seq_len):
    train_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                   end_date=training_end_date)
    val_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                 start_date=val_start_date, end_date=val_end_date)
    test_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                  start_date=testing_start_date)
    return train_sequences, val_sequences, test_sequences

In [21]:
testing_start_date = datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') 
val_start_date = testing_start_date - datetime.timedelta(days=30*4)
training_end_date = val_start_date - datetime.timedelta(days=1)
val_end_date = testing_start_date - datetime.timedelta(days=1)

In [22]:
nhead = 4

In [36]:
encoder_causality = True

In [37]:
train_sequences, val_sequences, test_sequences = create_train_val_test_sets(series_values, training_end_date, val_start_date, 
                                                                            val_end_date, testing_start_date,
                                                                           14, 7)
train_dataset = SequenceDatasetForTransformer(train_sequences, encoder_causality=encoder_causality)
train_dataloader = DataLoader(train_dataset, batch_size=8, shuffle=True)

In [38]:
vanilla_transformer_with_nullmask = Transformer(d_model=64, nhead=nhead, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)

In [39]:
optimizer = torch.optim.Adam(vanilla_transformer_with_nullmask.parameters())

In [40]:
save_path = '/home/mbaroody/Programming/Time series/TimeSeriesExperiments/v4-{}.pt'

In [41]:

epoch = 0
# prev_params = None
while True:
    running_loss = 0
    print("Epoch {}".format(epoch))
    for i, data in enumerate(train_dataloader):
        if ((i + 1) % 250 == 0):
            print("Reached batch {}, running_loss was {}".format(i+1, running_loss / 250))
            running_loss = 0
            
        encoder_input, decoder_input, ground_truth, ground_truth_null_indices,\
                encoder_sa_mask, decoder_sa_mask, decoder_encoder_null_mask = data
        
        
        encoder_input, decoder_input, encoder_sa_mask,\
                decoder_sa_mask, decoder_encoder_null_mask = format_input(encoder_input, decoder_input, encoder_sa_mask, 
                                                                          decoder_sa_mask, decoder_encoder_null_mask, nhead)
        optimizer.zero_grad()
        outputs = vanilla_transformer_with_nullmask(encoder_input, decoder_input, encoder_sa_mask, decoder_sa_mask, 
                                                    decoder_encoder_null_mask)
        # outputs is shape dec_len x bs x 1
        outputs = outputs.squeeze().T

            
        # delete items that are null in target
        losses_nonull_per_sequence = torch.sum(((outputs - ground_truth) * ground_truth_null_indices) ** 2, 1)
        batch_divide = ground_truth_null_indices.shape[1] - torch.sum(1 - ground_truth_null_indices, 1)
        losses_nonull = torch.mean(losses_nonull_per_sequence / batch_divide)
        
        losses_nonull.backward()
        optimizer.step()
        
#         flag = False
#         for param in vanilla_transformer_with_nullmask.parameters():
#             if torch.sum(torch.isnan(param.data)) > 0:
#                 flag = True
#                 break
#         if flag:
#             print('outputs')
#             print(outputs)
#             print('ground truth')
#             print(ground_truth)
#             print('ground truth null indices')
#             print(ground_truth_null_indices)
#             print('loss a')
#             print(losses_nonull_per_sequence)
#             print('batch divide')
#             print(batch_divide)
#             print('loss')
#             print(losses_nonull.item())
            
#             break
                
#         prev_params = vanilla_transformer_with_nullmask.parameters()
        
        running_loss += losses_nonull.item()

        
    print('Saving')
    torch.save(vanilla_transformer_with_nullmask.state_dict(), save_path.format(epoch))
    epoch += 1
        
    

Epoch 0
Reached batch 250, running_loss was 79.06778560638428
Reached batch 500, running_loss was 51.179389556884765
Reached batch 750, running_loss was 37.37841262817383
Reached batch 1000, running_loss was 40.77492350769043
Reached batch 1250, running_loss was 40.383444709777834
Reached batch 1500, running_loss was 36.412503072738645
Reached batch 1750, running_loss was 34.781448913574216
Reached batch 2000, running_loss was 33.51221705436706
Reached batch 2250, running_loss was 34.32927252578735
Reached batch 2500, running_loss was 33.79481966018677
Reached batch 2750, running_loss was 33.58684712982178
Reached batch 3000, running_loss was 32.362316875457765
Reached batch 3250, running_loss was 36.87517970657348
Reached batch 3500, running_loss was 32.95948349761963
Reached batch 3750, running_loss was 34.21847271347046
Reached batch 4000, running_loss was 29.59201545333862
Reached batch 4250, running_loss was 33.98009145355225
Reached batch 4500, running_loss was 31.888674238204956

Reached batch 2000, running_loss was 29.806238704681398
Reached batch 2250, running_loss was 28.03031008529663
Reached batch 2500, running_loss was 30.641440671920776
Reached batch 2750, running_loss was 29.55279969215393
Reached batch 3000, running_loss was 30.86311809539795
Reached batch 3250, running_loss was 29.258385364532472
Reached batch 3500, running_loss was 29.730132108688355
Reached batch 3750, running_loss was 26.688039253234862
Reached batch 4000, running_loss was 28.602966915130615
Reached batch 4250, running_loss was 30.16948080444336
Reached batch 4500, running_loss was 31.073651790618896
Reached batch 4750, running_loss was 30.700766967773436
Reached batch 5000, running_loss was 28.802714279174804
Reached batch 5250, running_loss was 28.676991682052613
Reached batch 5500, running_loss was 27.115360122680663
Reached batch 5750, running_loss was 27.20308097076416
Reached batch 6000, running_loss was 29.347605529785156
Reached batch 6250, running_loss was 28.9004223518371

KeyboardInterrupt: 

In [50]:
val_dataset = SequenceDatasetForTransformerTesting(val_sequences)
val_dataloader = DataLoader(val_dataset, batch_size=8, shuffle=True)

In [43]:
def create_null_mask_for_batch(in_seq, out_seq, is_self_attn=True):
    in_seq_len = in_seq.shape[1]
    out_seq_len = out_seq.shape[1]
    batch_size = in_seq.shape[0]
    null_indices = in_seq.isnan().nonzero()
    if len(null_indices) == 0:
        return torch.zeros((batch_size, out_seq_len, in_seq_len))
    else:
        mask = torch.zeros((batch_size, out_seq_len, in_seq_len))
        for i in range(batch_size):
            sequence_nulls =  null_indices[null_indices[:, 0] == i]
            sequence_nulls = sequence_nulls[:, 1]
            mask[i].index_fill_(1, sequence_nulls, float('-inf'))
            if is_self_attn:
                for index in sequence_nulls:
                    mask[i, index, index] = 0  # need this to prevent bug when null is in first position (of decoder self attn)
        return mask

In [44]:
def create_causality_mask_batch(dec_seq_len, bs):
    return TransformerModel.generate_square_subsequent_mask(dec_seq_len).unsqueeze(0).repeat(bs, 1, 1)

In [45]:
def create_batch_masks(enc_seq_batch, dec_seq_batch):
    # should be shape bs x seq_len
    enc_mask = create_null_mask_for_batch(enc_seq_batch, enc_seq_batch, is_self_attn=True)
    dec_sa_null_mask = create_null_mask_for_batch(dec_seq_batch, dec_seq_batch, is_self_attn=True)
    dec_sa_causality_mask = create_causality_mask_batch(dec_seq_batch.shape[1], dec_seq_batch.shape[0])
    dec_sa_mask = dec_sa_null_mask + dec_sa_causality_mask
    dec_enc_mask = create_null_mask_for_batch(enc_seq_batch, dec_seq_batch, is_self_attn=False)
    
    return enc_mask, dec_sa_mask, dec_enc_mask
    
    
    

In [174]:
# e, g, gi = next(iter(val_dataloader))
# print(e)

# d = e[:, -1].unsqueeze(-1)

# create_batch_masks(e, d)

In [54]:
# vanilla_transformer_with_nullmask_ = Transformer(d_model=64, nhead=nhead, num_encoder_layers=2, num_decoder_layers=2,
#                 dim_feedforward=256, dropout=0.1, activation=F.gelu)
vanilla_transformer_with_nullmask_ = Transformer(d_model=64, nhead=nhead, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)
vanilla_transformer_with_nullmask_.load_state_dict(torch.load('/home/mbaroody/Programming/Time series/TimeSeriesExperiments/v4-3.pt'))

<All keys matched successfully>

In [48]:
def evaluate_model(model, eval_dataloader, encoder_causality=False):
    model.eval()
    with torch.no_grad():
        total_loss = 0
        batch_count = 0
        for i, val_data in enumerate(eval_dataloader):  # todo refactor code to make val/test stepthroughs easier, remove redundant


            encoder_input, ground_truth, ground_truth_null_indices = val_data

            decoder_input = encoder_input[:, -1].unsqueeze(-1)
            enc_mask = create_null_mask_for_batch(encoder_input, encoder_input, is_self_attn=True)
            if encoder_causality:
                enc_sa_mask = create_causality_mask_batch(encoder_input.shape[1], encoder_input.shape[0])
                enc_mask = enc_mask + enc_sa_mask

            encoder_input = torch.nan_to_num(encoder_input)

            ground_truth = torch.nan_to_num(ground_truth)

            batch_errors = torch.zeros((ground_truth.shape[0], ground_truth.shape[1]))
            batch_predictions = torch.zeros((ground_truth.shape[0], ground_truth.shape[1]))
    #         print('enc input')
    #         print(encoder_input)
    #         print('ground truth')
    #         print(ground_truth)
            for h in range(ground_truth.shape[1]):
                dec_sa_null_mask = create_null_mask_for_batch(decoder_input, decoder_input, is_self_attn=True)
                dec_sa_causality_mask = create_causality_mask_batch(decoder_input.shape[1], decoder_input.shape[0])
                dec_sa_mask = dec_sa_null_mask + dec_sa_causality_mask
                dec_enc_mask = create_null_mask_for_batch(encoder_input, decoder_input, is_self_attn=False)
                decoder_input_ = torch.nan_to_num(decoder_input)

                encoder_input_, decoder_input_, enc_mask_, \
                    dec_sa_mask, dec_enc_mask = format_input(encoder_input, decoder_input_, 
                                                             enc_mask, dec_sa_mask, 
                                                             dec_enc_mask, nhead)
    #             print('dec in')
    #             print(decoder_input_)
    #             print(dec_sa_mask)
    #             print(dec_enc_mask)
                outputs = model(encoder_input_, decoder_input_, enc_mask_, dec_sa_mask, 
                                                            dec_enc_mask)
    #             print('outputs')
    #             print(outputs)
                if h > 0:
                    timestep_outputs = outputs.squeeze().T[:, h]
                else:
                    timestep_outputs = outputs.reshape(outputs.shape[0], outputs.shape[1]).T[:, h]
    #             print('latest')
    #             print(timestep_outputs)
                batch_predictions[:, h] = timestep_outputs
                timestep_batch_loss = (ground_truth[:, h] - timestep_outputs) ** 2
                batch_errors[:, h] = timestep_batch_loss

                decoder_input = torch.cat((decoder_input, timestep_outputs.unsqueeze(-1)), 1)

            losses_nonull_per_sequence = torch.sum(batch_errors, 1)
            batch_divide = ground_truth_null_indices.shape[1] - torch.sum(1 - ground_truth_null_indices, 1)
            error_nonull = torch.mean(losses_nonull_per_sequence / batch_divide)


            print('batch_predictions')
            print(batch_predictions)
            print('ground truth')
            print(ground_truth)
    #         print('batch error')
    #         print(error_nonull)
            batch_count += 1
            total_loss += error_nonull
        avg_loss = total_loss / batch_count
        return avg_loss

            
      
        

In [51]:
evaluate_model(vanilla_transformer_with_nullmask_, val_dataloader, encoder_causality=encoder_causality)

batch_predictions
tensor([[39.7324, 40.1827, 33.4770, 29.3647, 29.0814, 28.2421, 36.2364],
        [23.4058, 33.1547, 40.3623, 35.1886, 26.9763, 22.1588, 22.7864],
        [16.3108, 13.0066, 15.7317, 14.9797, 17.1447, 20.9447, 30.3867],
        [17.2823, 20.3815, 29.9368, 30.1558, 16.4632, 17.0013, 14.7735],
        [18.2353, 24.2265, 34.2950, 29.7136, 16.0194, 18.3915, 17.7236],
        [14.3601, 15.6162, 14.3060, 15.4450, 21.1630, 27.5691, 21.3094],
        [16.9266, 18.8469, 25.7142, 29.9132, 25.2900, 18.4843, 19.3121],
        [13.7636, 17.3571, 24.3512, 16.4217, 12.4746, 11.9286, 11.9821]])
ground truth
tensor([[ 2.7920,  4.5777, 33.6876, 12.1457, 22.4773, 23.1009, 32.9932],
        [21.7971, 40.3912, 56.8027, 45.4932, 37.8118, 30.4989, 26.0629],
        [31.3651, 12.4145, 17.9379, 19.3977, 14.1504, 21.8306, 35.9548],
        [20.1672, 11.7063, 37.7409, 48.9654, 22.7891, 20.2806,  9.1553],
        [14.7817, 30.5130, 44.4586,  0.0000, 15.2778, 18.5658, 20.4790],
        [ 0.0000,  

batch_predictions
tensor([[32.3337, 35.5807, 22.5141, 14.7143, 16.5846, 15.1842, 19.2186],
        [16.2578, 21.8546, 25.3921, 22.4328, 15.3888, 15.7359, 14.6118],
        [13.0849, 15.6244, 14.6949, 15.5995, 16.7833, 21.3619, 26.6184],
        [18.8399, 11.6734, 12.7592, 13.2151, 15.0331, 15.5408, 19.9649],
        [14.4486, 14.5702, 15.0183, 16.6305, 21.1939, 23.4572, 11.2312],
        [23.4987, 36.4754, 24.8249, 18.5034, 18.0603, 15.8117, 17.5707],
        [12.9021, 13.7842, 16.6863, 21.6792, 22.6988, 13.2371, 13.8243],
        [17.9878, 14.5884, 13.0957, 14.3285, 10.8224, 12.3311, 18.1670]])
ground truth
tensor([[31.1366, 32.4830, 26.9558,  9.8356, 12.1882, 13.6480, 14.1582],
        [17.1094, 18.8059, 30.0894, 22.3435, 16.9122, 15.7286, 18.1483],
        [12.6907, 17.1620, 12.3225, 14.8738, 19.3056, 24.7107, 29.0505],
        [27.7354, 16.0442, 16.2941, 11.8622, 11.0600, 12.8748, 21.5676],
        [13.0063, 11.9279, 15.2551, 14.7422, 23.1326, 25.9206, 11.9805],
        [29.3084, 3

tensor([[ 5.1623, 11.0138, 11.1697, 11.4073, 12.6343, 17.3518, 17.6539],
        [19.0050, 20.9226, 30.5079, 40.8449, 34.0592, 21.0600, 20.7165],
        [25.3500, 33.3030, 31.6987, 18.5864, 20.4046, 20.4195, 24.9651],
        [13.1794, 12.6658, 12.9785, 17.5768, 19.1716, 10.6787, 10.9536],
        [26.8457, 29.4347, 33.6902, 35.5428, 30.0075, 23.5333, 24.6579],
        [19.3830, 14.6829, 12.3386, 13.2239, 14.5474, 20.2126, 28.8895],
        [29.3740, 18.4630, 17.2197, 16.4155, 16.9308, 22.6183, 33.2261],
        [30.5825, 29.7803, 39.0148, 49.5706, 47.7942, 38.0658, 33.3081]])
ground truth
tensor([[ 5.7733, 16.5702, 12.9537, 12.0331, 18.6349, 21.7517, 19.3714],
        [15.9297, 18.0697, 34.8356, 58.2766, 45.3940, 33.0074, 30.0028],
        [ 4.1163,  3.1299, 17.9774,  7.5092, 19.6870, 20.6470, 25.3682],
        [12.9393, 11.8197, 12.1599, 17.0210, 24.4898, 21.7545, 10.8844],
        [21.3309, 27.4855, 31.6544, 39.1110, 24.6318, 17.5565, 30.8127],
        [20.6633, 32.1995, 24.5181, 3

batch_predictions
tensor([[29.3653, 31.9211, 40.3486, 49.0798, 45.4519, 37.0345, 32.8064],
        [10.8695, 11.9120, 14.2152, 11.4412,  9.2064,  9.8334,  8.5330],
        [13.2112, 16.7027, 19.4301, 17.1246, 12.9196, 13.9446, 13.2137],
        [16.1685, 15.5754, 16.2718, 18.6991, 19.1720, 11.8951, 14.9142],
        [11.5821, 15.8763, 15.4009, 15.2688, 17.5660, 25.6894, 27.1236],
        [12.9859, 12.6227, 12.7537, 13.4186, 14.5666, 18.6033, 14.2114],
        [16.5524, 16.3822, 23.4260, 31.4476, 32.3197, 17.8276, 18.2906],
        [12.5209, 12.1556, 12.5165, 15.0150, 19.9532, 19.6483, 11.5191]])
ground truth
tensor([[52.3668, 75.9495, 14.1440, 11.0402, 25.2409, 19.1185, 28.7557],
        [10.9548,  8.3114, 16.7675, 14.8080,  8.5876,  8.5481,  8.1010],
        [ 9.7317, 16.3861, 23.8164, 22.7249, 14.9527, 18.7007, 12.0068],
        [14.2162, 16.6228, 15.9653, 23.3956, 25.8548, 11.5729, 14.4003],
        [ 9.9947, 18.5692, 19.3188, 20.0026, 17.7801, 28.1694, 30.2604],
        [12.9274, 1

batch_predictions
tensor([[28.3612, 11.9317, 15.2749, 15.0651, 15.7491, 21.7815, 30.1640],
        [16.9335, 21.9890, 26.8988, 14.6581, 15.3547, 14.7495, 14.6566],
        [10.0856,  7.9993,  7.0102,  6.7958,  7.0137,  8.0387, 10.8899],
        [18.2539, 18.7539, 20.3553, 25.3431, 26.3219, 14.9034, 18.9088],
        [23.2148, 22.7592, 20.4957, 21.9716, 20.8957, 15.1053, 14.9535],
        [17.9745, 17.6300, 18.4353, 24.9910, 35.6650, 35.3902, 18.9036],
        [25.3239, 16.7362, 16.4287, 19.1841, 19.5858, 20.4090, 24.0727],
        [33.4546, 31.4880, 13.7611, 17.1232, 16.1972, 18.0510, 24.7028]])
ground truth
tensor([[41.3730, 10.4550, 17.1357, 13.6639, 11.9542, 26.4729, 38.1773],
        [17.4908, 27.5513, 28.7217, 14.9921, 15.3209, 18.2272, 16.2415],
        [ 9.9348,  5.6831,  4.4218,  3.6706,  4.4076,  6.3917,  9.6372],
        [30.2209, 30.6812,  3.9584,  5.0237, 13.2036,  6.6412, 18.0037],
        [17.3330, 25.2236, 20.0815, 26.1441, 24.1320,  8.4298, 12.1646],
        [19.0760, 1

...

batch_predictions
tensor([[31.1480, 36.2321, 35.3454, 27.8725, 30.5205, 27.5216, 26.6278],
        [32.9953, 20.2353, 17.6045, 17.4790, 19.8314, 26.9729, 35.8949],
        [24.4626, 21.3055, 24.1079, 34.7947, 41.5347, 38.9473, 24.9747],
        [31.9244, 42.4318, 27.9572, 23.4321, 20.5886, 20.1032, 23.5673],
        [27.4675, 30.2302, 26.6084, 16.9393, 18.9654, 20.5665, 24.3000],
        [12.4543, 14.3849, 13.7032, 14.8557, 18.6221, 24.3313, 18.9834],
        [21.0908, 25.2822, 21.8732, 13.6783, 14.3646, 14.2934, 15.7920],
        [10.3463, 12.5722,  8.6145,  6.6773,  5.8304,  6.6019,  6.7154]])
ground truth
tensor([[31.4834, 41.1099, 39.2820, 29.0900, 29.2346, 28.0642, 29.5634],
        [43.8453, 17.4513, 15.3735, 15.0842, 22.2777, 26.4729, 46.2914],
        [40.2353, 50.4535, 47.5907,  2.7920,  4.5777, 33.6876, 12.1457],
        [38.2795, 55.3713, 43.1406, 28.8832, 32.1003, 24.3481, 27.8770],
        [ 6.2217,  5.7256, 13.9456,  7.9507, 19.9546, 17.6587, 25.1417],
        [12.1740, 1

batch_predictions
tensor([[ 9.0131,  9.9937,  9.5163, 10.9722, 12.7240, 16.1357, 15.7886],
        [19.7534, 19.4784, 14.1078, 13.4853, 12.1108, 11.7449, 14.3870],
        [43.5341, 47.2178, 39.2644, 34.2188, 36.1118, 39.0836, 39.5359],
        [16.4994, 14.9911, 16.9530, 23.7151, 32.0417, 22.4974, 14.0402],
        [25.5734, 25.7120, 14.3019, 15.5624, 15.3249, 15.5432, 20.4999],
        [38.0606, 26.1154, 22.5705, 25.0480, 29.9845, 39.4903, 42.4787],
        [40.4238, 18.4000, 19.3889, 17.8562, 20.0506, 30.0043, 46.1031],
        [23.9378, 20.5968, 12.9704, 13.7805, 13.5487, 15.1093, 19.7943]])
ground truth
tensor([[ 7.4171, 11.6123, 10.3104, 11.7307, 10.9548, 14.6239,  5.7996],
        [23.0931, 22.6591, 14.2951, 14.3872, 10.6128, 10.9811, 13.3219],
        [48.4350, 61.8885, 58.7059, 27.5776, 56.4440, 39.7422, 30.9837],
        [14.9660, 12.1882, 16.0431, 29.4785, 45.4507, 31.7035, 15.4620],
        [23.6849, 28.5113, 12.9274, 13.1378, 10.5602, 16.8990, 19.8580],
        [51.5731, 4

batch_predictions
tensor([[15.2624, 14.1639,  9.8009,  8.4372,  9.3637,  9.7065, 10.6691],
        [19.2892, 19.6461, 12.3825, 12.7126, 10.6508, 11.3016, 13.6895],
        [33.1477, 16.0129, 20.1299, 18.0018, 20.0034, 30.8144, 35.7731],
        [13.5555, 17.3489, 20.5438, 10.6654, 13.1291, 12.8552, 10.2973],
        [25.8192, 19.4509, 17.4574, 15.4623, 16.5152, 24.7404, 36.0495],
        [12.6346, 19.5151, 18.2293, 17.8859, 20.9247, 28.9951, 30.5772],
        [14.5766, 17.0272, 15.9961, 16.3361, 18.5402, 26.2409, 30.8980],
        [24.0181, 18.6132, 17.9376, 17.4659, 22.1555, 31.4289, 30.5251]])
ground truth
tensor([[13.5850, 12.3225,  7.2330,  8.9164,  7.0752,  5.4840,  7.6933],
        [20.0421, 19.2267,  3.5245,  9.1005,  8.2983, 10.8759, 16.2283],
        [31.4484, 15.2636, 15.7738, 18.9768, 16.2840, 32.6956, 41.4824],
        [12.6644, 16.5045, 23.7507, 20.2130, 16.2546, 12.1778, 10.5997],
        [31.4768, 19.0051, 16.8367, 13.8605, 14.9802, 31.8736, 49.6457],
        [10.5584, 2

batch_predictions
tensor([[14.0366, 14.2541, 14.3066, 14.7148, 19.6838, 25.5863, 13.7837],
        [20.0625, 30.1886, 24.0333, 13.3522, 14.7800, 12.9407, 14.4017],
        [16.0931, 19.7840, 25.3108, 20.9769, 14.0939, 15.5735, 13.9445],
        [16.0209, 18.3586, 20.6511, 25.2841, 27.9306, 12.5989, 17.5967],
        [25.3003, 23.4822, 22.7424, 28.9137, 42.7150, 39.7611, 24.1213],
        [22.8549, 32.3672, 28.2291, 14.7015, 18.4631, 18.8783, 16.5783],
        [15.3453, 20.1040, 13.2207, 11.5484, 10.0490,  8.5139, 11.6642],
        [16.9887, 16.5455, 18.1926, 26.2444, 21.6806, 16.9131, 17.8660]])
ground truth
tensor([[13.6054, 14.5266, 12.7976,  8.8294, 21.3294, 31.8736, 31.4484],
        [22.6757, 40.3486, 37.0040, 20.4790, 21.3294, 31.0658, 36.2528],
        [12.3299, 17.9280, 20.6066, 18.9909, 10.8418, 13.8747, 11.2812],
        [14.7817, 18.7075, 20.2381, 29.0958,  3.5998, 12.9677, 15.5329],
        [ 8.8577, 13.6905, 22.6332, 34.6088, 50.6661, 46.4286, 27.3810],
        [26.3545, 3

tensor(79.7747)

In [55]:
test_dataset = SequenceDatasetForTransformerTesting(test_sequences)
test_dataloader = DataLoader(test_dataset, batch_size=8, shuffle=True)

In [56]:
evaluate_model(vanilla_transformer_with_nullmask_, test_dataloader, encoder_causality=encoder_causality)

batch_predictions
tensor([[22.1771, 34.4582, 44.8772, 25.9733, 21.7029, 21.2547, 19.5553],
        [36.8802, 36.1286, 12.6004, 15.7763, 15.6215, 15.7772, 21.1368],
        [21.5604, 29.2440, 28.7017, 16.2675, 17.6960, 15.9569, 16.4904],
        [33.1258, 16.8547, 18.6037, 16.7708, 20.8429, 35.8431, 48.5800],
        [33.9833, 28.6188, 31.4902, 39.1149, 46.2199, 50.9829, 47.3872],
        [24.1578, 10.0502, 13.0063, 12.5410, 12.9372, 18.3746, 31.6111],
        [13.5777, 15.8519, 25.1355, 27.5033,  9.6382, 13.1102, 13.1232],
        [29.6623, 32.2600, 21.2895, 19.3225, 17.9875, 17.2012, 19.8468]])
ground truth
tensor([[20.8837, 32.1936, 56.7596, 53.1036, 29.5371, 24.8948, 20.8969],
        [43.4524, 38.3929, 19.0051, 19.2744, 12.7126, 21.8679, 24.0788],
        [17.2804, 28.3272, 31.4834, 17.3461, 16.9779, 14.1767, 17.7275],
        [43.3107, 19.7846, 20.5782, 14.5975, 20.3798, 36.1536, 51.8849],
        [41.6491, 42.5829, 45.9890, 42.5565, 49.4345, 49.9211, 39.3740],
        [25.6803, 1

batch_predictions
tensor([[15.5842, 21.2663, 29.8220, 24.4215, 12.9773, 14.5629, 13.9883],
        [12.5921, 21.8803, 20.1765,  6.7041,  8.4279,  9.2058, 10.3396],
        [23.0246, 16.0621, 11.5454, 11.3136, 11.2164, 12.3928, 16.4560],
        [17.3630, 22.7473, 23.1574, 25.7855, 16.4138, 16.9408, 16.1709],
        [15.2246, 12.9621, 13.7205, 15.2224, 19.2421, 28.3171, 28.6975],
        [14.2381, 16.1181, 23.3567, 31.2161, 32.6730, 12.3735, 15.7982],
        [31.6802, 34.3491,  8.1711, 14.4761, 15.3362, 16.6844, 21.4998],
        [ 9.5539, 10.7359, 18.0034, 18.7640,  7.1780,  7.4424,  8.6846]])
ground truth
tensor([[11.0731, 22.9353, 11.9542, 31.3125, 10.6654,  0.0000, 10.2578],
        [11.7964, 23.1983, 22.5802,  6.6938, 10.4156,  7.6802, 10.4550],
        [19.8185, 13.3482, 11.2441,  9.6923, 10.5339, 13.6639, 12.3225],
        [14.1636, 14.4661, 24.8685, 21.1862, 12.7564,  9.2451, 18.0431],
        [18.3673, 10.5584, 10.9694, 12.1740, 15.0510, 22.4065, 31.3917],
        [18.8350, 2

batch_predictions
tensor([[26.8848, 25.7983, 14.4655, 17.2576, 16.2151, 16.0713, 21.7104],
        [ 8.7871,  9.2125,  9.8631, 10.9479, 13.2874, 16.6957, 11.5960],
        [11.4998, 12.3261, 21.6345, 28.7725, 20.4605, 11.0797, 12.2334],
        [ 8.8054, 10.5014, 11.4152, 16.7617, 13.9410,  5.1909,  5.4051],
        [15.1606, 28.8469, 37.2602, 25.4666, 13.9368, 14.1789, 14.0363],
        [ 8.5392,  8.8435,  9.1924, 15.4687, 20.1639, 14.3862,  7.6921],
        [18.9404, 17.4120, 10.6313, 12.2768, 12.6421, 14.5669, 20.0149],
        [12.8403, 13.1605, 18.8431, 25.6271, 25.0096, 11.2214, 14.5471]])
ground truth
tensor([[33.0357, 11.1678, 12.0890, 14.0306, 15.9439, 17.2761, 25.1984],
        [ 8.2851, 11.1783, 12.6249,  7.5092, 12.5066, 17.8590,  9.7449],
        [ 7.0578,  9.8781, 19.6712, 29.5777, 23.2426, 10.2041, 11.4938],
        [14.3566, 15.0368, 13.7046, 14.6825, 20.9467,  2.2251,  3.0329],
        [14.1865, 31.5051, 40.1644, 25.4819,  7.9790, 11.6497, 12.9819],
        [10.3175, 1

batch_predictions
tensor([[13.2000, 16.7770, 26.0313, 31.0657,  8.1231, 12.6526, 12.3473],
        [16.2863, 23.4763, 25.6828, 11.0013, 12.6394, 12.3128, 14.1099],
        [ 7.6911,  6.2632,  7.6177,  8.1390,  9.3069, 13.8554, 19.6204],
        [29.0726, 23.6244, 16.5906, 16.7265, 16.3284, 16.0243, 25.8797],
        [29.6828,  9.2144, 13.4395, 14.1275, 15.7642, 17.7099, 29.8718],
        [ 9.7149,  9.8873, 11.0195, 16.6486, 21.4277, 15.3013,  7.3844],
        [25.2001, 32.1197, 36.9222, 26.8193, 21.7651, 20.3840, 20.6190],
        [11.2779, 12.4280, 14.2585, 20.2739, 23.8701, 11.3624, 11.2183]])
ground truth
tensor([[12.2567, 19.0952, 27.7749, 24.9737,  4.9842,  6.8911, 12.8748],
        [17.1485, 26.1763, 31.2358, 19.1893, 18.1264, 13.2795, 11.6071],
        [ 2.2357,  0.0000,  7.8248,  9.4555, 12.3751, 12.4277, 28.9584],
        [35.9836, 36.4796, 16.2982, 15.0794, 20.8050, 18.4099, 24.2205],
        [ 4.9745,  5.2438, 12.3583, 13.9598, 16.5675, 21.9246, 33.4042],
        [ 9.0347,  

batch_predictions
tensor([[14.9993, 20.5641, 31.8934, 31.1210, 12.0680, 13.9329, 14.6317],
        [ 9.6439, 13.2842, 12.6770, 13.1543, 17.1056, 31.1296, 29.6172],
        [16.2486, 16.1949, 16.4305, 21.8056, 29.6092, 28.8976, 12.1661],
        [20.3541, 22.6691, 34.2868, 43.3190, 42.7889, 25.1851, 20.4885],
        [32.9642, 18.0537, 19.8891, 21.2718, 24.7263, 34.9576, 42.6559],
        [ 6.7038,  7.4770,  8.8657, 13.3600, 16.1047, 19.1093,  5.7984],
        [14.1721, 17.5515, 16.6435, 17.1591, 20.1209, 27.3630, 27.3590],
        [38.9875, 25.3218, 22.2764, 21.4653, 24.5057, 33.7237, 45.6218]])
ground truth
tensor([[13.4637, 19.8129, 40.4337, 35.2608, 19.0476, 16.8651, 15.1786],
        [ 7.1712, 15.3912, 10.9410, 12.8118, 22.5198, 32.2137, 22.5198],
        [16.4519, 18.2667, 16.6360, 24.4740, 36.4545, 34.9947, 14.7422],
        [20.5418, 23.3693, 58.2588, 43.2272, 38.2956, 22.6328, 25.6839],
        [32.4566, 15.3603,  3.2614, 12.0989, 18.3588, 24.7107, 41.0968],
        [ 3.3305,  

...

batch_predictions
tensor([[26.4462, 15.2018, 15.9017, 15.5526, 15.6010, 16.6034, 23.7594],
        [18.8230, 34.3010, 34.1835, 15.6587, 15.0795, 14.1243, 14.6042],
        [13.1484, 22.3751, 20.0123,  9.2140, 10.7792,  8.5516,  9.8760],
        [17.7191, 27.1317, 28.9136, 10.9839, 14.9329, 13.5906, 14.7224],
        [ 9.9216, 13.7015, 16.3799,  8.6826,  6.5826,  7.6362,  8.2657],
        [30.9692, 10.0095, 15.6959, 16.3324, 17.3502, 24.6495, 31.7667],
        [22.6429, 32.6836, 37.8689,  9.4238, 15.7556, 14.8661, 16.4070],
        [11.9459,  7.3712,  6.0737,  8.1032,  8.3401,  8.8376,  9.9922]])
ground truth
tensor([[36.6649, 20.5813, 19.4371, 15.0973, 16.3861, 13.9795, 18.4640],
        [13.7755, 30.1871, 27.5652, 11.6922, 13.7188, 10.7001, 11.4654],
        [13.4212, 17.9422,  4.3651,  6.6043,  9.8498,  8.8577,  9.0986],
        [20.0539, 28.6990, 35.4025, 10.5867, 12.2449, 10.8702, 13.6905],
        [ 9.5213, 13.2693, 15.0447, 13.0852,  6.8780, 11.0205,  8.8901],
        [40.4195, 1

batch_predictions
tensor([[21.4302, 19.8552, 23.4202, 42.3647, 45.2647, 39.4092, 23.9189],
        [21.8136, 10.6551, 12.7988, 12.3721, 12.6375, 18.3005, 25.0928],
        [18.4979, 19.1343, 36.5092, 44.9608, 26.6644, 19.9207, 19.6195],
        [30.1756, 15.9518, 16.6401, 15.5375, 16.3912, 20.8716, 32.8414],
        [12.0739, 14.1114, 14.5555, 18.9809, 27.6034, 28.2605, 22.1004],
        [11.4055, 14.4717, 14.6692, 16.0709, 19.9060, 27.5449, 22.8667],
        [14.8255, 16.0095, 18.8103, 25.4497, 29.3800, 27.3309, 14.1240],
        [13.3721, 22.4573, 33.5011, 28.0877, 10.8881, 13.0726, 13.1278]])
ground truth
tensor([[20.2130, 19.9369, 18.8848, 33.9427, 55.6418, 14.1899,  0.0000],
        [29.8264,  9.9290, 12.0857, 12.4277, 11.0205, 19.8185, 22.8432],
        [26.3282, 17.3856, 34.0873, 63.3877, 44.1610, 13.9137, 12.0594],
        [29.6344, 12.0040, 14.7251, 15.4195, 19.8271, 22.2222, 27.7636],
        [ 7.1712,  7.7806, 11.6355, 14.5975, 19.8554, 30.8957,  8.9569],
        [10.8759, 1

batch_predictions
tensor([[13.1244, 19.1539, 26.6584, 26.1682,  9.8699, 11.4936, 12.2322],
        [21.7187, 32.5185, 30.2025,  8.3939, 14.6894, 13.8466, 15.9717],
        [13.4233, 13.1203, 13.2069, 17.4764, 25.6618, 28.7325, 17.0914],
        [15.2418, 16.2887, 36.0728, 36.8410, 20.2468, 18.2094, 17.0941],
        [26.1803, 12.7003, 14.0080, 12.6181, 13.0122, 19.7656, 34.3223],
        [27.2798, 10.5639, 14.2737, 12.7895, 13.7490, 17.0409, 26.3530],
        [15.6300, 23.2157, 25.4309,  9.1569, 11.8892, 11.0029, 13.2206],
        [15.2298, 15.8683, 18.3384, 25.9079, 28.1211, 11.2851, 15.0196]])
ground truth
tensor([[ 6.0757, 10.8364, 18.6349, 27.3672,  0.0000,  3.7480, 11.5071],
        [19.6287, 40.8588, 39.0023, 12.6842, 16.7092,  8.2483, 16.2698],
        [11.7063, 11.6497, 10.1049, 17.1910, 29.9178, 32.9790, 14.0448],
        [21.5420, 36.0261, 36.7914, 25.6094, 18.4382, 21.9388, 10.5867],
        [19.6287,  9.0703, 12.6276,  8.5459, 10.4025, 19.8129, 31.0941],
        [30.8957, 1

batch_predictions
tensor([[22.7057, 34.2864, 27.7873, 11.0577, 13.4351, 12.9040, 15.6189],
        [11.2627, 14.8729, 16.3566, 19.4983, 22.0275, 29.3392, 27.4602],
        [20.6402, 28.6048, 24.8230, 12.7210, 14.5205, 13.1483, 14.6794],
        [20.7439, 19.8492, 10.3573, 10.9758, 10.7547, 12.9617, 13.8932],
        [16.5907, 16.1569,  7.0762,  8.6960,  7.8568,  7.5668, 11.8696],
        [11.4052, 11.5978, 12.2279, 17.8657, 27.1599, 17.0795,  7.9310],
        [20.2194,  9.8868, 10.7020,  9.9570, 11.0086, 19.7566, 30.2071],
        [17.5527, 17.0351, 16.4617, 17.3096, 27.6639, 45.6638, 40.8849]])
ground truth
tensor([[20.6633, 31.1791, 29.1525, 12.3724, 12.4150, 14.9518, 16.8226],
        [13.1247, 18.3588, 10.1131, 19.7791, 19.8185, 26.5255, 29.7212],
        [20.0964, 27.3810, 26.6298, 13.4354, 16.3974, 18.3390, 13.6905],
        [26.9726, 19.1347, 13.3351, 11.2835, 10.2709, 16.0442, 20.5550],
        [15.7812, 12.6644,  4.9185,  9.5213,  6.4308,  7.5618, 13.4008],
        [ 9.1005, 1

tensor(33.1955)

In [34]:
class TransformerVanilla(Module):
    
    
    def __init__(self, d_model=64, nhead=4, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=512, dropout=0.1, activation=F.gelu, use_norm=True):
        
        super(TransformerVanilla, self).__init__()
        self.transformer_model = TransformerModel(d_model=d_model, nhead=nhead, num_encoder_layers=num_encoder_layers,
                                                  num_decoder_layers=num_decoder_layers, dim_feedforward=dim_feedforward,
                                                  dropout=dropout, activation=activation, use_norm=use_norm)
        
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        self.input_projection1 = nn.Linear(1, d_model)
        self.input_projection2 = nn.Linear(d_model, d_model)
        self.output_projection = nn.Linear(d_model, 1)
        
    def forward(self, encoder_x, decoder_x, src_mask=None, tgt_mask=None, memory_mask=None):
        """ encoder_x should be vector of size input_seq_len x bs x 1   
            decoder_x should be vector of size output_seq_len x bs x 1
        """
        encoder_x = self.pos_encoder(self.input_projection2(self.input_projection1(encoder_x)))
        decoder_x = self.pos_encoder(self.input_projection2(self.input_projection1(decoder_x)))
        x = self.transformer_model(encoder_x, decoder_x, 
                                   src_mask=src_mask, tgt_mask=tgt_mask, memory_mask=memory_mask)
        x = self.output_projection(x)
        return x

    
        
        
        

In [40]:
model_v0 = TransformerVanilla(d_model=64, nhead=nhead, num_encoder_layers=2, num_decoder_layers=2,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)
model_v0.load_state_dict(torch.load('/home/mbaroody/Programming/Time series/NN5/transformer_vanilla_robustnull_v2-0.pt'))

<All keys matched successfully>

In [41]:
evaluate_model(model_v0, test_dataloader)

batch_predictions
tensor([[11.4240, 11.7356, 12.1022, 12.5022, 12.9190, 13.3243, 13.6408],
        [30.6787, 31.0758, 31.0345, 30.9378, 30.8638, 30.8237, 30.8084],
        [24.8778, 28.7262, 28.5320, 27.3244, 25.2732, 22.0480, 19.4626],
        [17.6461, 22.5739, 21.3124, 19.0141, 16.4467, 15.1427, 15.2202],
        [17.6647, 22.7957, 23.0727, 22.1033, 20.5371, 18.5566, 17.1777],
        [23.0011, 20.9399, 21.2400, 21.9991, 22.6732, 23.2022, 23.6021],
        [16.7230, 19.8401, 19.2410, 18.3349, 17.5219, 16.9240, 16.5867],
        [23.4345, 30.0252, 29.5433, 27.4890, 23.3897, 18.2426, 18.3207]])
ground truth
tensor([[13.5718, 20.6865,  9.6791,  6.8780,  6.9306,  8.3246, 11.8096],
        [24.9079, 29.5634, 34.5739, 45.1604, 18.3456, 21.1073, 22.9616],
        [15.0085, 27.8770, 36.7772, 37.0890, 21.1026, 15.2920, 16.2557],
        [18.0414, 15.5612, 12.9960, 16.9218, 23.0867, 32.1854, 14.1865],
        [21.3010, 35.1332, 33.7302, 13.0244, 12.7976, 12.6842, 13.4070],
        [30.8107, 2

batch_predictions
tensor([[20.8067, 29.1103, 29.0137, 27.0325, 22.3041, 17.1467, 17.3533],
        [20.4119, 21.0035, 20.8544, 20.5631, 20.3071, 20.1406, 20.0661],
        [18.7933, 19.9496, 19.6146, 19.0784, 18.6161, 18.3035, 18.1501],
        [25.6364, 26.1793, 26.1036, 25.8755, 25.6469, 25.4806, 25.3933],
        [20.4224, 21.5751, 21.3344, 20.8683, 20.4482, 20.1543, 20.0001],
        [16.5220, 15.1254, 15.5129, 16.2160, 16.8156, 17.2842, 17.6458],
        [21.0843, 20.0166, 19.7710, 19.9387, 20.2758, 20.6641, 21.0583],
        [24.3506, 28.5611, 28.0166, 26.7180, 24.9353, 22.3779, 20.2739]])
ground truth
tensor([[ 0.0000,  0.0000, 14.8384, 35.4025, 33.6593,  8.3617, 17.2761],
        [13.0527, 15.3345, 29.7761, 26.7999, 15.3345, 18.1122, 14.6117],
        [13.9795, 11.9411, 15.5576, 25.6575, 24.8816, 12.1778, 10.2841],
        [39.5125,  6.8736,  7.3838, 20.8192, 11.5930, 15.8022, 20.1531],
        [13.4271, 15.5445, 28.0247, 14.8211, 32.1278, 22.5013, 23.4482],
        [10.6786,  

batch_predictions
tensor([[19.3798, 19.5794, 19.5151, 19.3745, 19.2441, 19.1614, 19.1317],
        [13.2030, 12.7601, 12.5901, 12.5640, 12.6394, 12.7661, 12.9356],
        [ 5.0716,  4.3449,  4.3207,  4.3548,  4.3802,  4.3972,  4.4094],
        [21.3347, 22.3822, 22.1543, 21.6611, 21.1784, 20.8125, 20.5986],
        [19.8892, 19.7796, 19.8053, 19.8418, 19.8704, 19.8978, 19.9288],
        [23.1622, 25.5485, 25.1959, 24.4085, 23.5533, 22.7522, 22.1007],
        [30.2627, 27.7034, 27.1310, 27.5492, 28.2811, 29.0354, 29.7161],
        [17.9935, 23.7863, 22.9267, 20.7469, 17.5588, 16.0552, 16.3224]])
ground truth
tensor([[22.5013, 20.5024, 10.5734,  8.8769,  8.6796, 14.2951, 18.6612],
        [ 3.4850,  7.9695,  6.3914,  9.6002, 13.9269, 20.3577, 15.1105],
        [ 5.2721,  7.7239,  7.5113,  7.8656,  8.9569, 14.9660,  9.0703],
        [16.6754, 19.8054, 20.7391, 25.1578, 26.9726, 13.5192, 17.7012],
        [31.5623, 28.9453, 12.6381, 16.4256, 16.9385, 16.7806, 18.3719],
        [19.7279, 2

batch_predictions
tensor([[20.2508, 27.6320, 26.7556, 23.8845, 18.5791, 16.6841, 16.9938],
        [38.2789, 38.2719, 38.2730, 38.2732, 38.2730, 38.2728, 38.2728],
        [27.2057, 27.4831, 27.5000, 27.4149, 27.2873, 27.1776, 27.1157],
        [33.5748, 33.1687, 33.1489, 33.2084, 33.2730, 33.3416, 33.4157],
        [13.6617, 17.3827, 21.8854, 20.6916, 18.5013, 16.0529, 14.6150],
        [27.2129, 23.6230, 24.6123, 25.9462, 27.1088, 28.0112, 28.6583],
        [19.7465, 22.5189, 21.8739, 20.7657, 19.5445, 18.3660, 17.5782],
        [14.6181, 18.3109, 21.6524, 21.6582, 20.8906, 19.9369, 19.0848]])
ground truth
tensor([[16.5308, 18.2272, 17.1357, 25.2367, 37.9143, 25.9732, 12.2699],
        [58.4824, 60.6786, 56.6149, 65.8469, 52.4066, 44.9763, 55.1683],
        [13.8605, 17.7296, 13.3645, 15.6179, 40.0652, 53.6706, 24.0930],
        [29.7761, 38.5913, 18.5232, 19.3594, 23.0584, 26.9558, 38.6480],
        [10.5865,  9.5476, 10.0736, 18.5429, 27.4987, 28.8795, 11.9279],
        [14.3566, 4

batch_predictions
tensor([[26.4438, 34.9929, 37.1497, 36.4311, 34.6646, 31.0433, 25.2181],
        [23.2849, 26.6935, 26.1826, 24.8922, 23.0697, 20.8058, 19.2951],
        [13.6317, 12.8158, 13.3054, 14.0125, 14.6529, 15.0863, 15.3150],
        [13.4826, 17.2232, 20.0377, 20.9034, 20.6201, 20.0474, 19.5135],
        [31.1340, 29.8622, 29.4667, 29.5090, 29.7636, 30.1602, 30.6656],
        [20.8650, 21.4058, 21.2585, 20.9730, 20.7182, 20.5501, 20.4744],
        [19.4218, 18.3223, 18.1901, 18.5944, 19.1965, 19.8561, 20.5217],
        [19.0463, 22.0281, 20.9729, 19.3279, 17.3585, 15.7995, 15.5283]])
ground truth
tensor([[33.3640, 53.8532, 47.3567, 22.7117, 20.9232, 16.7938, 20.8443],
        [ 4.3226, 37.1457, 34.5947, 14.6117, 19.7279, 14.3991, 19.0760],
        [13.5850,  9.9816,  9.6923, 10.8890, 11.6781, 16.1494, 23.4219],
        [ 0.0000, 12.9819, 25.3118,  7.7098,  9.3396, 12.4858, 18.4240],
        [ 8.9164, 16.4256, 14.6370, 31.2599, 58.8901, 47.5802, 12.2830],
        [19.3027, 2

...

batch_predictions
tensor([[19.7079, 21.1487, 20.6311, 19.9035, 19.2437, 18.7436, 18.4513],
        [21.2092, 26.2578, 25.4429, 23.1622, 19.2768, 16.8451, 17.0719],
        [21.3137, 27.3300, 26.3208, 23.7923, 19.2296, 16.5596, 16.8733],
        [13.6585, 16.7017, 19.4812, 18.5223, 17.2685, 16.1352, 15.2386],
        [22.2343, 22.4217, 22.4190, 22.3253, 22.2130, 22.1279, 22.0869],
        [21.4733, 21.4613, 21.4607, 21.4596, 21.4580, 21.4560, 21.4668],
        [17.7892, 22.5658, 23.7495, 21.9313, 18.2385, 15.1352, 14.8216],
        [23.4149, 20.5983, 20.9156, 21.9754, 23.0083, 23.8950, 24.6228]])
ground truth
tensor([[13.0102, 21.1026, 24.3197, 18.2540, 13.8180, 12.7409, 11.8056],
        [17.2902, 12.9677, 12.0890, 24.2347, 28.6848, 41.6525, 22.2222],
        [22.3781, 19.3027, 25.9779, 33.6735, 41.1423,  7.4688, 18.0556],
        [11.0205,  7.5881, 10.5471, 11.3230, 24.2109, 29.6028,  8.2720],
        [39.3740, 16.0179, 18.2930, 21.4624, 14.6633, 21.6728, 28.5113],
        [18.0272, 2

batch_predictions
tensor([[17.5629, 21.5274, 20.0976, 17.7681, 15.1275, 13.9333, 13.9012],
        [38.3899, 38.3587, 38.3666, 38.3698, 38.3711, 38.3720, 38.3730],
        [24.9087, 28.4616, 28.3253, 27.2843, 25.6301, 23.2812, 20.9403],
        [21.8366, 19.4721, 19.5490, 20.4864, 21.4518, 22.3171, 23.0788],
        [17.9087, 17.5730, 17.6024, 17.7250, 17.8526, 17.9649, 18.0606],
        [18.9633, 18.1753, 18.0533, 18.2212, 18.4778, 18.7446, 18.9961],
        [14.6515, 14.2414, 14.3246, 14.5710, 14.8478, 15.0987, 15.2981],
        [19.1450, 19.4013, 19.3383, 19.1968, 19.0711, 18.9932, 18.9636]])
ground truth
tensor([[ 9.1662, 15.3472, 20.3840, 23.9085,  5.0237, 10.7180,  8.3377],
        [42.5039, 56.3388, 23.0668,  0.0000, 29.9579, 43.4377, 46.8701],
        [22.9748, 43.0037, 42.7012, 17.3330, 18.4903, 15.9390, 22.3304],
        [36.0969,  6.7460, 14.0590, 14.7251, 18.8067, 21.1876, 37.0040],
        [26.8141, 26.7432, 17.0777, 12.3441, 15.3628, 13.0102, 21.1026],
        [23.0867, 1

batch_predictions
tensor([[23.5074, 25.8062, 25.4845, 24.5385, 23.2999, 21.9071, 20.6611],
        [11.8905, 13.8543, 16.5695, 17.8503, 16.9927, 16.1418, 15.4808],
        [17.3331, 16.8840, 16.8811, 17.0167, 17.1662, 17.3013, 17.4181],
        [24.4895, 29.5520, 29.0227, 27.5336, 25.2343, 21.7544, 19.7968],
        [10.4884, 11.5283, 12.6438, 14.2265, 16.2702, 16.3914, 15.7870],
        [29.0145, 28.4841, 28.3836, 28.4622, 28.5997, 28.7761, 28.9811],
        [19.0618, 19.7135, 19.3871, 18.8428, 18.3432, 17.9965, 17.8316],
        [18.3967, 22.6904, 22.1921, 21.1268, 19.9289, 18.9009, 18.3013]])
ground truth
tensor([[14.7422, 15.1631, 25.1578, 26.9069, 27.9853, 15.4787, 17.4382],
        [11.3361, 13.3877, 14.4266, 16.2283, 24.3556, 23.2378,  6.5623],
        [11.1961, 12.6701, 15.4337, 15.4195, 15.5612, 27.0408, 17.0210],
        [18.7533, 22.0410, 29.4845, 44.7002, 34.2451, 21.2388, 20.1078],
        [ 9.0986,  6.9728, 11.4371, 20.5074, 17.1202,  4.6910, 10.3175],
        [51.7715, 3

batch_predictions
tensor([[28.6590, 30.1266, 30.1227, 29.7369, 29.2613, 28.8291, 28.5020],
        [30.7605, 36.6681, 36.7319, 36.1108, 35.3245, 34.4918, 33.6482],
        [13.7242, 13.3830, 14.4571, 15.5258, 16.2304, 16.5435, 16.6681],
        [15.7956, 15.8385, 15.8223, 15.7830, 15.7482, 15.7326, 15.7350],
        [15.8835, 19.6559, 20.8388, 20.1222, 19.2337, 18.4131, 17.7684],
        [15.4641, 19.4472, 21.0162, 20.3168, 19.4104, 18.5510, 17.8422],
        [16.3740, 18.6976, 18.2902, 17.3790, 16.4904, 15.7603, 15.2475],
        [20.8158, 20.8549, 20.8480, 20.8057, 20.7582, 20.7297, 20.7279]])
ground truth
tensor([[16.7375, 18.1548, 19.3169, 25.5952, 47.6332, 14.7534,  0.0000],
        [24.8299, 29.9178, 44.8413, 49.2914,  7.4405, 13.5771, 21.7545],
        [18.6612,  4.7212,  7.8248,  9.1399, 10.6128, 11.7964, 23.1983],
        [17.4119, 16.7149,  6.3782,  8.9164, 10.7180, 14.1899, 25.9469],
        [12.0465, 19.2885, 30.4280, 22.6616, 11.3237, 14.3566, 11.1395],
        [11.8359, 1

tensor(75.5777)

In [ ]:
e, d, t, gn, ea, da, dea = se, d, t, gn, ea, da, dea = sequence_iter(dl, 3)
print(gn)

In [ ]:
t = torch.Tensor([[1, np.nan], [2, 2], [np.nan, np.nan]]).isnan().nonzero().T
print(t)
t[1][t[0] == 0]


In [ ]:
d = SequenceDatasetForTransformer(train_sequences)
dl = DataLoader(d, batch_size=8, shuffle=True)

In [ ]:
e, d, t, ea, da, dea = next(iter(dl))

In [ ]:
t

In [ ]:
ea.repeat(3, 1, 1).shape

In [ ]:
process_batch_nulls(e,d,t)

In [ ]:
# testing this vanilla transformer. 
# Note that to batch, examples within a single batch must have same enc and dec input lengths
test_transformer = Transformer()
test_encoder_x = torch.unsqueeze(torch.Tensor([[1, 2, 3], [7, 8, 9]]).T, -1)
test_decoder_x = torch.unsqueeze(torch.Tensor([[0, 4], [0, 10]]).T, -1)
ground_truth = torch.Tensor([[4, 5], [10, 11]]).T
test_dec_output = torch.squeeze(test_transformer(test_encoder_x, test_decoder_x), -1)
# ground truth and output are now output_len x bs
test_loss = F.mse_loss(test_dec_output, ground_truth)
test_loss.backward()


In [ ]:
input1 = torch.Tensor([0, 1, 2, 3, 4])
input2 = torch.Tensor([0, 1, 2, 3, 4])
w1 = torch.nn.Parameter(torch.Tensor([[0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4], 
                                      [0, 1, 2, 3, 4]]), requires_grad=True)
output1 = input1 @ w1
output2 = input2 @ w1
target1 = torch.Tensor([3, 4, 1, np.nan, 4])
target2 = torch.Tensor([3, np.nan, 1, np.nan, 4])
loss1 = F.mse_loss(output1, target1, reduction='none')
loss_without_nan1 = loss1[~torch.isnan(loss1)]
loss2 = F.mse_loss(output2, target2, reduction='none')
loss_without_nan2 = loss2[~torch.isnan(loss2)]
losses = torch.cat((loss_without_nan1, loss_without_nan2), 0)
final_loss = torch.sum(losses) / (len(loss_without_nan1) + len(loss_without_nan2))
final_loss.backward()


In [ ]:
w1.grad

In [ ]:
input1 = torch.Tensor([2, 1, 2, 3, 4])
input2 = torch.Tensor([3, 1, 2, 3, 4])
w1 = torch.nn.Parameter(torch.Tensor([[5, 1, 2, 3, 4],
                                     [5, 1, 2, 3, 4],
                                     [6, 1, 2, 3, 4],
                                     [8, 1, 2, 3, 4], 
                                      [9, 1, 2, 3, 4]]), requires_grad=True)
output1 = input1 @ w1
output2 = input2 @ w1
target1 = torch.Tensor([3, 4, np.nan, 4, 4])
indices1 = list((~target1.isnan()).nonzero(as_tuple=True))
output1_nonull = output1[indices1]
target1_nonull = target1[indices1]
target2 = torch.Tensor([3, np.nan, 1, np.nan, 4])
indices2 = list((~target2.isnan()).nonzero(as_tuple=True))
output2_nonull = output2[indices2]
target2_nonull = target2[indices2]
loss1 = F.mse_loss(output1_nonull, target1_nonull)
loss2 = F.mse_loss(output2_nonull, target2_nonull)
final_loss = (loss1 + loss2) / 2
final_loss.backward()


In [ ]:
loss1

In [ ]:
# pytorch test

inputs = torch.Tensor([4, 0, 7])
weights_vec1 = torch.nn.Parameter(torch.Tensor([[5, 4, 2], [3, 4, 1], [5, 3, 2], [1, 2, 3]]), requires_grad=True)
weights_vec2 = torch.nn.Parameter(torch.Tensor([[1, 2, 3], [4, 5, 6], [2, 3, 2], [4, 3, 1]]), requires_grad=True)
vec3 = torch.Tensor([[1, 2, 3], [4, 5, 6], [2, 3, 2], [4, 3, 1]])
q = weights_vec1 * inputs
k = weights_vec2 * inputs
logits = (q.T @ k) + torch.Tensor([[0, float('-inf'), 0], [0, float('-inf'), 0], [0, float('-inf'), 0]])
logits = logits / 1000  # div by 1000 just for stability for demonstration
logits.retain_grad()
print('logits: ', logits, '\n')
soft = torch.nn.functional.softmax(logits, dim=1)
soft.retain_grad()
print('softmax: ', soft, '\n')
logits2 = (soft @ vec3.T) @ vec3 + torch.Tensor([[0, float('-inf'), 0], [0, float('-inf'), 0], [0, float('-inf'), 0]])
print('logits2: ', logits2, '\n')
soft2 = torch.nn.functional.softmax(logits2, dim=1)
print('softmax: ', soft2, '\n')
final_m = (soft2 @ vec3.T).T
print('final m: ', final_m, '\n')

final = torch.sum(final_m)  # just to get some scalar value at the end
print('final: ', final, '\n')
final.backward()
print('soft gradients: ', soft.grad, '\n')
print('logits gradients: ', logits.grad, '\n')
print('wq gradients: ', weights_vec1.grad, '\n')
print('wk gradients: ', weights_vec2.grad, '\n')

In [ ]:
# pytorch test

inputs = torch.Tensor([4, 0, 7])
weights_vec1 = torch.nn.Parameter(torch.Tensor([5, 4, 2]), requires_grad=True)
weights_vec2 = torch.nn.Parameter(torch.Tensor([1, 2, 3]), requires_grad=True)
q = torch.unsqueeze(weights_vec1, 1) @ torch.unsqueeze(inputs, 1).T
k = torch.unsqueeze(weights_vec2, 1) @ torch.unsqueeze(inputs, 1).T
q.retain_grad()
k.retain_grad()
logits = (q.T @ k) + torch.Tensor([[0, float('-inf'), 0], [0, 0, 0], [0, float('-inf'), 0]])
logits = torch.cat([logits[:1], logits[2:]]) / 1000  # div by 1000 just for stability for demonstration
logits.retain_grad()
print('logits: ', logits, '\n')
soft = torch.nn.functional.softmax(logits, dim=1)
soft = torch.cat([soft[:1], torch.Tensor([[0, 0, 0]]), soft[1:]])
soft.retain_grad()
print('softmax: ', soft, '\n')
final = torch.sum(torch.prod(soft + 1, dim=0))  # just to get some scalar value at the end
print('final: ', final, '\n')
final.backward()
print('soft gradients: ', soft.grad, '\n')
print('logits gradients: ', logits.grad, '\n')
print('q gradients: ', q.grad, '\n')
print('k gradients: ', k.grad, '\n')
print('wq gradients: ', weights_vec1.grad, '\n')
print('wk gradients: ', weights_vec2.grad, '\n')

In [ ]:
# for decoder w1 -- projecting from scalar to matrix dimensionwise

tens1 = torch.Tensor([1, 2])  # timesteps
tens2 = torch.Tensor([1, 2, 3, 4])  # pos encoding
tens1 = tens1.repeat(4, 1)
tens1.T * tens2

In [ ]:
t1 = torch.Tensor([[1, 2], [1 ,2], [1, 2]])
t2 = torch.Tensor([[1, 4], [2 ,5], [3, 6], [4, 5]])


In [ ]:
t1 = torch.Tensor([[1, 2, 3, 4], [5, 6, 7, 8]])
v = torch.nn.Parameter(torch.Tensor([3, 3.1, 3.2, 3.4]), requires_grad=True)
z = t1 * v
s = F.softmax(z, dim=1)
i_ = torch.multinomial(s, 1).squeeze()
print(i_)
selected = torch.cat((torch.unsqueeze(z[0][i_[0]], -1) , torch.unsqueeze(z[1][i_[1]], -1)))
target = torch.Tensor([4, 8])
l = torch.mean(target - z.T[i_])
l.backward()

In [ ]:
z

In [ ]:
v.grad

In [328]:
l = nn.LayerNorm(4)
t = torch.Tensor([[[1, 2, 3, 4], [2, 4, 6, 8]], [[1, 2, 3, 4], [2, 4, 4.2, 5.3]]])
l(t)

tensor([[[-1.3416, -0.4472,  0.4472,  1.3416],
         [-1.3416, -0.4472,  0.4472,  1.3416]],

        [[-1.3416, -0.4472,  0.4472,  1.3416],
         [-1.5752,  0.1050,  0.2730,  1.1971]]],
       grad_fn=<NativeLayerNormBackward>)

In [333]:
p = PositionalEncoding(64, max_len=5000)
p.pe

tensor([[[ 0.0000e+00,  1.0000e+00,  0.0000e+00,  ...,  1.0000e+00,
           0.0000e+00,  1.0000e+00]],

        [[ 8.4147e-01,  5.4030e-01,  6.8156e-01,  ...,  1.0000e+00,
           1.3335e-04,  1.0000e+00]],

        [[ 9.0930e-01, -4.1615e-01,  9.9748e-01,  ...,  1.0000e+00,
           2.6670e-04,  1.0000e+00]],

        ...,

        [[ 9.5625e-01, -2.9254e-01,  6.4315e-01,  ...,  6.3049e-01,
           6.1813e-01,  7.8608e-01]],

        [[ 2.7050e-01, -9.6272e-01, -5.1133e-02,  ...,  6.3036e-01,
           6.1823e-01,  7.8599e-01]],

        [[-6.6395e-01, -7.4778e-01, -7.1816e-01,  ...,  6.3022e-01,
           6.1834e-01,  7.8591e-01]]])